In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
%pip install -U peft datasets sacrebleu bitsandbytes

## **Original model performance | Base Model and Full-fine-tuning translations and evaluation**

In [ ]:
import os
import pandas as pd
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def load_data_from_directory(base_path):
    data = []
    file_path = os.path.join(base_path, 'test_split.csv')

    # Read the CSV file
    df = pd.read_csv(file_path)
    hindi_sentences = df['Hindi_Text'].tolist()
    english_sentences = df['English_Text'].tolist()
    data.extend(zip(hindi_sentences, english_sentences))

    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    return model, tokenizer

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer = load_model()

    print("Loading test data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    test_data = load_data_from_directory(base_path)

    print("Evaluating the model.")
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for mBART Evaluation:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/mbart_evaluation_results.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Loading test data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [08:10<00:00,  3.11it/s]


Summary of Results for mBART Evaluation:
         avg_inference_time_sec  meteor_score  chrf_score
Overall                0.314512      0.253451    0.202371
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/mbart_evaluation_results.csv


In [ ]:
# Meteor and chrF scores calculated here were wrong. The model was not configured correctly to translate Hindi to English. The below code corrects these scores-

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import nltk
from collections import defaultdict
import torch
from multiprocessing import Pool
import gc
from google.colab import drive
from transformers import MBartForConditionalGeneration, MBartTokenizer


# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('punkt_tab')

# Check if GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def translate_with_model(texts, model, tokenizer, max_length=100, batch_size=32):
    all_translations = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        # Set source language to Hindi and target language to English
        tokenizer.src_lang = "hi_IN"  # Hindi language code
        tokenizer.tgt_lang = "en_XX"  # English language code

        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

        # Force the model to translate to English
        forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

        with torch.no_grad():
            translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

        batch_translations = tokenizer.batch_decode(translated, skip_special_tokens=True)
        all_translations.extend(batch_translations)
    return all_translations

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())

    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100

    return {
        'meteor': meteor,
        'chrf': chrf_score
    }

def calculate_metrics_wrapper(args):
    reference, candidate = args
    return calculate_metrics(reference, candidate)

def evaluate_model(model, tokenizer, test_data, model_name):
    all_scores = defaultdict(list)
    all_translations = []

    print(f"\nEvaluating {model_name}:")
    hindi_texts, english_texts = zip(*test_data)

    translations = translate_with_model(hindi_texts, model, tokenizer)

    # Use multiprocessing for metric calculation
    with Pool() as pool:
        scores_list = pool.map(calculate_metrics_wrapper, zip(english_texts, translations))

    for hindi, english, translation, scores in zip(hindi_texts, english_texts, translations, scores_list):
        for metric, score in scores.items():
            all_scores[metric].append(score)

        all_translations.append({
            'hindi': hindi,
            'english_reference': english,
            'english_translation': translation,
            'scores': scores
        })

    return all_scores, all_translations

def process_csv_files(root_dir):
    results = {}

    for primary_category in os.listdir(root_dir):
        primary_category_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_category_path):
            results[primary_category] = {}

            for sentence_type in os.listdir(primary_category_path):
                sentence_type_path = os.path.join(primary_category_path, sentence_type)
                if os.path.isdir(sentence_type_path):
                    results[primary_category][sentence_type] = {}

                    for file in os.listdir(sentence_type_path):
                        if file.endswith('.csv'):
                            tense = os.path.splitext(file)[0]
                            file_path = os.path.join(sentence_type_path, file)

                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))

                            results[primary_category][sentence_type][tense] = data

    return results

def aggregate_results(results, model_name):
    aggregated = {
        'primary_category': [],
        'sentence_type': [],
        'tense': [],
        'meteor': [],
        'chrf': []
    }

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                aggregated['primary_category'].append(primary_category)
                aggregated['sentence_type'].append(sentence_type)
                aggregated['tense'].append(tense)
                for metric in ['meteor', 'chrf']:
                    aggregated[metric].append(np.mean([translation['scores'][metric] for translation in data['translations']]))

    df = pd.DataFrame(aggregated)

    # Convert score columns to numeric, coercing errors to NaN
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    # Global performance for each primary category
    global_primary = df.groupby('primary_category')[score_columns].mean().reset_index()
    global_primary['category'] = 'Global Primary Category'

    # Global performance for each sentence type
    global_sentence_type = df.groupby('sentence_type')[score_columns].mean().reset_index()
    global_sentence_type['category'] = 'Global Sentence Type'

    # Global performance for each tense
    global_tense = df.groupby('tense')[score_columns].mean().reset_index()
    global_tense['category'] = 'Global Tense'

    # Combine all results
    all_results = pd.concat([df, global_primary, global_sentence_type, global_tense], sort=False)
    print(all_results)

    # Save results to CSV in Google Drive
    csv_filename = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/basemodel_performance.csv'
    all_results.to_csv(csv_filename, index=False)
    print(f"Results for {model_name} have been saved to '{csv_filename}'")

    return all_results

def get_worst_performers(results, n=6):
    worst_performers = defaultdict(lambda: defaultdict(list))

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                for translation in data['translations']:
                    for metric, score in translation['scores'].items():
                        worst_performers[primary_category][metric].append((score, translation))

    for primary_category in worst_performers:
        for metric in worst_performers[primary_category]:
            worst_performers[primary_category][metric].sort(key=lambda x: x[0])
            worst_performers[primary_category][metric] = worst_performers[primary_category][metric][:n]

    return worst_performers

def print_worst_performers(worst_performers, model_name):
    print(f"\n--- Worst Performers for {model_name} ---")
    for primary_category, metrics in worst_performers.items():
        print(f"\nPrimary Category: {primary_category}")
        for metric, performers in metrics.items():
            print(f"\n  Metric: {metric}")
            for i, (score, translation) in enumerate(performers, 1):
                print(f"    {i}. Score: {score:.4f}")
                print(f"       Hindi Text: {translation['hindi']}")
                print(f"       English Reference: {translation['english_reference']}")
                print(f"       Model Translation: {translation['english_translation']}")

def main():
    # Load models
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"
    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    # Process CSV files from Google Drive
    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted/test_set')

    # Evaluate models
    marianmt_results = {}

    for primary_category, sentence_types in test_data.items():
        marianmt_results[primary_category] = {}
        for sentence_type, tenses in sentence_types.items():
            print(f"Evaluating {primary_category} - {sentence_type}")
            marianmt_results[primary_category][sentence_type] = {}
            for tense, data in tenses.items():
                print(f"Evaluating {primary_category} - {sentence_type} - {tense}")
                try:
                    marianmt_scores, marianmt_translations = evaluate_model(model, tokenizer, data, "mBART")

                    marianmt_results[primary_category][sentence_type][tense] = {
                        'scores': marianmt_scores,
                        'translations': marianmt_translations
                    }
                except Exception as e:
                    print(f"Error processing {primary_category} - {sentence_type} - {tense}: {str(e)}")
                    marianmt_results[primary_category][sentence_type][tense] = {'error': str(e)}

                # Clear GPU memory after processing each tense
                clear_gpu_memory()

    # Get worst performers
    marianmt_worst = get_worst_performers(marianmt_results)

    # Print worst performers
    print_worst_performers(marianmt_worst, "mBART")

    # Aggregate and save results
    marianmt_all_results = aggregate_results(marianmt_results, "mBART")

    # Print summary
    for model_name, results in [("MarianMT", marianmt_all_results)]:
        print(f"\nSummary of Results for {model_name}:")
        for category in ['Global Primary Category', 'Global Sentence Type', 'Global Tense']:
            print(f"\n{category} Performance:")
            summary = results[results['category'] == category]
            mean_scores = summary[['meteor', 'chrf']].mean()
            print(mean_scores)

if __name__ == "__main__":
    main()

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cuda
Evaluating Standard Sentences - Exclamatory Sentences
Evaluating Standard Sentences - Exclamatory Sentences - past_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - past_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_present

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_past

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_future

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_continuous

Eva

In [ ]:
# Global Primary Category Performance was choosen for comparison.

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import nltk
from collections import defaultdict
import torch
from multiprocessing import Pool
import gc
from google.colab import drive
from transformers import MBartForConditionalGeneration, MBartTokenizer


# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('punkt_tab')

# Check if GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def translate_with_model(texts, model, tokenizer, max_length=100, batch_size=32):
    all_translations = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        # Set source language to Hindi and target language to English
        tokenizer.src_lang = "hi_IN"  # Hindi language code
        tokenizer.tgt_lang = "en_XX"  # English language code

        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

        # Force the model to translate to English
        forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

        with torch.no_grad():
            translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

        batch_translations = tokenizer.batch_decode(translated, skip_special_tokens=True)
        all_translations.extend(batch_translations)
    return all_translations

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())

    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100

    return {
        'meteor': meteor,
        'chrf': chrf_score
    }

def calculate_metrics_wrapper(args):
    reference, candidate = args
    return calculate_metrics(reference, candidate)

def evaluate_model(model, tokenizer, test_data, model_name):
    all_scores = defaultdict(list)
    all_translations = []

    print(f"\nEvaluating {model_name}:")
    hindi_texts, english_texts = zip(*test_data)

    translations = translate_with_model(hindi_texts, model, tokenizer)

    # Use multiprocessing for metric calculation
    with Pool() as pool:
        scores_list = pool.map(calculate_metrics_wrapper, zip(english_texts, translations))

    for hindi, english, translation, scores in zip(hindi_texts, english_texts, translations, scores_list):
        for metric, score in scores.items():
            all_scores[metric].append(score)

        all_translations.append({
            'hindi': hindi,
            'english_reference': english,
            'english_translation': translation,
            'scores': scores
        })

    return all_scores, all_translations

def process_csv_files(root_dir):
    results = {}

    for primary_category in os.listdir(root_dir):
        primary_category_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_category_path):
            results[primary_category] = {}

            for sentence_type in os.listdir(primary_category_path):
                sentence_type_path = os.path.join(primary_category_path, sentence_type)
                if os.path.isdir(sentence_type_path):
                    results[primary_category][sentence_type] = {}

                    for file in os.listdir(sentence_type_path):
                        if file.endswith('.csv'):
                            tense = os.path.splitext(file)[0]
                            file_path = os.path.join(sentence_type_path, file)

                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))

                            results[primary_category][sentence_type][tense] = data

    return results

def aggregate_results(results, model_name):
    aggregated = {
        'primary_category': [],
        'sentence_type': [],
        'tense': [],
        'meteor': [],
        'chrf': []
    }

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                aggregated['primary_category'].append(primary_category)
                aggregated['sentence_type'].append(sentence_type)
                aggregated['tense'].append(tense)
                for metric in ['meteor', 'chrf']:
                    aggregated[metric].append(np.mean([translation['scores'][metric] for translation in data['translations']]))

    df = pd.DataFrame(aggregated)

    # Convert score columns to numeric, coercing errors to NaN
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    # Global performance for each primary category
    global_primary = df.groupby('primary_category')[score_columns].mean().reset_index()
    global_primary['category'] = 'Global Primary Category'

    # Global performance for each sentence type
    global_sentence_type = df.groupby('sentence_type')[score_columns].mean().reset_index()
    global_sentence_type['category'] = 'Global Sentence Type'

    # Global performance for each tense
    global_tense = df.groupby('tense')[score_columns].mean().reset_index()
    global_tense['category'] = 'Global Tense'

    # Combine all results
    all_results = pd.concat([df, global_primary, global_sentence_type, global_tense], sort=False)
    print(all_results)

    # Save results to CSV in Google Drive
    csv_filename = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/basemodel_performance.csv'
    all_results.to_csv(csv_filename, index=False)
    print(f"Results for {model_name} have been saved to '{csv_filename}'")

    return all_results

def main():
    # Load models
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"
    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    # Process CSV files from Google Drive
    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    # Evaluate models
    marianmt_results = {}

    for primary_category, sentence_types in test_data.items():
        marianmt_results[primary_category] = {}
        for sentence_type, tenses in sentence_types.items():
            print(f"Evaluating {primary_category} - {sentence_type}")
            marianmt_results[primary_category][sentence_type] = {}
            for tense, data in tenses.items():
                print(f"Evaluating {primary_category} - {sentence_type} - {tense}")
                try:
                    marianmt_scores, marianmt_translations = evaluate_model(model, tokenizer, data, "mBART")

                    marianmt_results[primary_category][sentence_type][tense] = {
                        'scores': marianmt_scores,
                        'translations': marianmt_translations
                    }
                except Exception as e:
                    print(f"Error processing {primary_category} - {sentence_type} - {tense}: {str(e)}")
                    marianmt_results[primary_category][sentence_type][tense] = {'error': str(e)}

                # Clear GPU memory after processing each tense
                clear_gpu_memory()

    # Aggregate and save results
    marianmt_all_results = aggregate_results(marianmt_results, "mBART")

    # Print summary
    for model_name, results in [("MarianMT", marianmt_all_results)]:
        print(f"\nSummary of Results for {model_name}:")
        for category in ['Global Primary Category', 'Global Sentence Type', 'Global Tense']:
            print(f"\n{category} Performance:")
            summary = results[results['category'] == category]
            mean_scores = summary[['meteor', 'chrf']].mean()
            print(mean_scores)

if __name__ == "__main__":
    main()

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cuda
Evaluating Standard Sentences - Exclamatory Sentences
Evaluating Standard Sentences - Exclamatory Sentences - past_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - past_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_present

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_past

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_future

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_continuous

Eva

Base Model Translation

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import MBartForConditionalGeneration, MBartTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
import nltk
import torch
import gc
import time
from tqdm import tqdm
from collections import defaultdict
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download NLTK data
nltk.download('punkt_tab')
nltk.download('wordnet')

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    start_time = time.time()
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=max_length, forced_bos_token_id=forced_bos_token_id)
    end_time = time.time()

    translation = tokenizer.batch_decode(outputs, skip_special_tokens=True)[0]
    return translation, end_time - start_time

def calculate_metrics(reference, candidate):
    ref_tokens = nltk.word_tokenize(reference.lower())
    cand_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([ref_tokens], cand_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

def process_csv_files(root_dir):
    results = {}
    for primary_category in os.listdir(root_dir):
        primary_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_path):
            results[primary_category] = {}
            for sentence_type in os.listdir(primary_path):
                sentence_path = os.path.join(primary_path, sentence_type)
                if os.path.isdir(sentence_path):
                    results[primary_category][sentence_type] = {}
                    for file in os.listdir(sentence_path):
                        if file.endswith(".csv"):
                            tense = file[:-4]
                            file_path = os.path.join(sentence_path, file)
                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))
                            results[primary_category][sentence_type][tense] = data
    return results

def aggregate_results(results, model_name, memory_usage_mb, avg_inference_time):
    rows = []
    for primary_category, types in results.items():
        for sentence_type, tenses in types.items():
            for tense, data in tenses.items():
                rows.append({
                    'primary_category': primary_category,
                    'sentence_type': sentence_type,
                    'tense': tense,
                    'meteor': data['scores']['meteor'],
                    'chrf': data['scores']['chrf']
                })

    df = pd.DataFrame(rows)
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    global_stats = df[score_columns].mean().to_dict()
    global_stats['model_gpu_memory_MB'] = memory_usage_mb
    global_stats['avg_inference_time_sec'] = avg_inference_time

    out_path = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/{model_name}_metrics.csv'
    df.to_csv(out_path, index=False)
    print(f"\nSaved detailed results to {out_path}")

    print("\n--- Overall Evaluation Summary ---")
    for k, v in global_stats.items():
        print(f"{k}: {v:.4f}" if isinstance(v, float) else f"{k}: {v}")
    return df, global_stats

def main():

    torch.cuda.empty_cache()
    # torch.cuda.reset_peak_memory_stats()

    model_dir = 'facebook/mbart-large-50-many-to-many-mmt'
    tokenizer = MBartTokenizer.from_pretrained(model_dir)
    model = MBartForConditionalGeneration.from_pretrained(model_dir)
    model.to(device)

    # torch.cuda.synchronize()
    time.sleep(2)
    peak_memory = torch.cuda.max_memory_allocated() / (1024 * 1024)

    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    results = {}
    all_inference_times = []

    for pc, types in test_data.items():
        results[pc] = {}
        for st, tenses in types.items():
            results[pc][st] = {}
            for tense, data in tenses.items():
                print(f"Evaluating: {pc} - {st} - {tense}")
                try:
                    metrics = evaluate_model(model, tokenizer, data)
                    results[pc][st][tense] = {'scores': {
                        'meteor': metrics['meteor'],
                        'chrf': metrics['chrf']
                    }}
                    all_inference_times.append(metrics['avg_inference_time'])
                except Exception as e:
                    print(f"Error: {e}")
                    results[pc][st][tense] = {'scores': {'meteor': 0.0, 'chrf': 0.0}}
                clear_gpu_memory()

    avg_inference_time = np.mean(all_inference_times)
    aggregate_results(results, "fine_tuned_mbart", peak_memory, avg_inference_time)

if __name__ == "__main__":
    main()

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cpu
Evaluating: Standard Sentences - Exclamatory Sentences - past_perfect


100%|██████████| 8/8 [00:37<00:00,  4.66s/it]


Evaluating: Standard Sentences - Exclamatory Sentences - present_perfect


100%|██████████| 8/8 [00:38<00:00,  4.86s/it]


...

Evaluating: Standard Sentences - Exclamatory Sentences - simple_past


100%|██████████| 8/8 [00:31<00:00,  3.95s/it]


Evaluating: Standard Sentences - Exclamatory Sentences - simple_future


 57%|█████▋    | 4/7 [00:21<00:16,  5.36s/it]


KeyboardInterrupt: 

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer

# Check for GPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Load model and tokenizer
model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"
tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

def translate_texts(hindi_texts, model, tokenizer, max_length=100, batch_size=32):
    all_translations = []
    tokenizer.src_lang = "hi_IN"  # Hindi
    tokenizer.tgt_lang = "en_XX"  # English
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    for i in range(0, len(hindi_texts), batch_size):
        batch = hindi_texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

        with torch.no_grad():
            translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

        decoded = tokenizer.batch_decode(translated, skip_special_tokens=True)
        all_translations.extend(decoded)

    return all_translations

# Example usage:
if __name__ == "__main__":
    hindi_sentences = [
        "हम भोजन कर रहे होंगे!",
        "क्या तुमने खाना खा लिया था?",
        "वह उल्टा चोर कोतवाल को डाँट रहा था!",
        "उसे ऊँची दुकान फीका पकवान मिला!",
        "क्या वैज्ञानिकों ने नई खोज की है?",
        "टीम नई सुविधाओं का परीक्षण करती है।"
    ]
    english_translations = translate_texts(hindi_sentences, model, tokenizer)
    for hi, en in zip(hindi_sentences, english_translations):
        print(f"Hindi: {hi}\nEnglish: {en}\n")


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Using device: cuda
Hindi: हम भोजन कर रहे होंगे!
English: We shall eat!

Hindi: क्या तुमने खाना खा लिया था?
English: Did you eat?

Hindi: वह उल्टा चोर कोतवाल को डाँट रहा था!
English: On the contrary, the thief was beating the Kotwal.

Hindi: उसे ऊँची दुकान फीका पकवान मिला!
English: He found a flour cooker in the high store.

Hindi: क्या वैज्ञानिकों ने नई खोज की है?
English: What have scientists discovered?

Hindi: टीम नई सुविधाओं का परीक्षण करती है।
English: Tests new facilities.



Full fine-tuning model evaluation and translation

In [ ]:
# The code below shows how the full-fine tuned model improved.

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

hindi_texts = [
    "हम भोजन कर रहे होंगे!",
    "क्या तुमने खाना खा लिया था?",
    "वह उल्टा चोर कोतवाल को डाँट रहा था!",
    "उसे ऊँची दुकान फीका पकवान मिला!",
    "क्या वैज्ञानिकों ने नई खोज की है?",
    "टीम नई सुविधाओं का परीक्षण करती है।"
]

print("full fine-tuned mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
full fine-tuned mBART translations:
Original: हम भोजन कर रहे होंगे!
Translated: We will be eating food!
Original: क्या तुमने खाना खा लिया था?
Translated: Had you eaten the food?
Original: वह उल्टा चोर कोतवाल को डाँट रहा था!
Translated: He was accusing others of his crime!
Original: उसे ऊँची दुकान फीका पकवान मिला!
Translated: He found all that glitters is gold!
Original: क्या वैज्ञानिकों ने नई खोज की है?
Translated: Has scientists made a new discovery?
Original: टीम नई सुविधाओं का परीक्षण करती है।
Translated: The team tests new features.


In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import MBartForConditionalGeneration, MBartTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
import nltk
import torch
import gc
import time
from tqdm import tqdm
from collections import defaultdict
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download NLTK data
nltk.download('punkt_tab')
nltk.download('wordnet')

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    start_time = time.time()
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=max_length, forced_bos_token_id=forced_bos_token_id)
    end_time = time.time()

    translation = tokenizer.batch_decode(outputs, skip_special_tokens=True)[0]
    return translation, end_time - start_time

def calculate_metrics(reference, candidate):
    ref_tokens = nltk.word_tokenize(reference.lower())
    cand_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([ref_tokens], cand_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

def process_csv_files(root_dir):
    results = {}
    for primary_category in os.listdir(root_dir):
        primary_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_path):
            results[primary_category] = {}
            for sentence_type in os.listdir(primary_path):
                sentence_path = os.path.join(primary_path, sentence_type)
                if os.path.isdir(sentence_path):
                    results[primary_category][sentence_type] = {}
                    for file in os.listdir(sentence_path):
                        if file.endswith(".csv"):
                            tense = file[:-4]
                            file_path = os.path.join(sentence_path, file)
                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))
                            results[primary_category][sentence_type][tense] = data
    return results

def aggregate_results(results, model_name, memory_usage_mb, avg_inference_time):
    rows = []
    for primary_category, types in results.items():
        for sentence_type, tenses in types.items():
            for tense, data in tenses.items():
                rows.append({
                    'primary_category': primary_category,
                    'sentence_type': sentence_type,
                    'tense': tense,
                    'meteor': data['scores']['meteor'],
                    'chrf': data['scores']['chrf']
                })

    df = pd.DataFrame(rows)
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    global_stats = df[score_columns].mean().to_dict()
    global_stats['model_gpu_memory_MB'] = memory_usage_mb
    global_stats['avg_inference_time_sec'] = avg_inference_time

    out_path = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/{model_name}_metrics.csv'
    df.to_csv(out_path, index=False)
    print(f"\nSaved detailed results to {out_path}")

    print("\n--- Overall Evaluation Summary ---")
    for k, v in global_stats.items():
        print(f"{k}: {v:.4f}" if isinstance(v, float) else f"{k}: {v}")
    return df, global_stats

def main():
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    torch.cuda.empty_cache()
    torch.cuda.reset_peak_memory_stats()

    model_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart"
    model = MBartForConditionalGeneration.from_pretrained(model_dir)
    model.to(device)

    torch.cuda.synchronize()
    time.sleep(2)
    peak_memory = torch.cuda.max_memory_allocated() / (1024 * 1024)

    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    results = {}
    all_inference_times = []

    for pc, types in test_data.items():
        results[pc] = {}
        for st, tenses in types.items():
            results[pc][st] = {}
            for tense, data in tenses.items():
                print(f"Evaluating: {pc} - {st} - {tense}")
                try:
                    metrics = evaluate_model(model, tokenizer, data)
                    results[pc][st][tense] = {'scores': {
                        'meteor': metrics['meteor'],
                        'chrf': metrics['chrf']
                    }}
                    all_inference_times.append(metrics['avg_inference_time'])
                except Exception as e:
                    print(f"Error: {e}")
                    results[pc][st][tense] = {'scores': {'meteor': 0.0, 'chrf': 0.0}}
                clear_gpu_memory()

    avg_inference_time = np.mean(all_inference_times)
    aggregate_results(results, "fine_tuned_mbart", peak_memory, avg_inference_time)

if __name__ == "__main__":
    main()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Using device: cuda
Evaluating: Standard Sentences - Exclamatory Sentences - past_perfect


100%|██████████| 8/8 [00:08<00:00,  1.06s/it]


Evaluating: Standard Sentences - Exclamatory Sentences - present_perfect


...

Evaluating: Voice and Speech Constructions - Active Voice - simple_past


100%|██████████| 15/15 [00:03<00:00,  4.98it/s]


Evaluating: Voice and Speech Constructions - Active Voice - simple_present


100%|██████████| 15/15 [00:03<00:00,  4.20it/s]



Saved detailed results to /content/drive/MyDrive/Colab Notebooks/Translation Models/results/fine_tuned_mbart_metrics.csv

--- Overall Evaluation Summary ---
meteor: 0.8044
chrf: 0.7381
model_gpu_memory_MB: 4707.3779
avg_inference_time_sec: 0.2877


## **Full fine-tuning | LoRA and QLoRA translations and evaluation**

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before fine-tuning: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Ensure all parameters are trainable
    for param in model.parameters():
        param.requires_grad = True

    before_fine_tuning = get_gpu_memory_usage()
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=4,
        per_device_eval_batch_size=8,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=5e-5,
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_fine_tuning
    print(f"Full fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)

    print(f"Trainable parameters after full fine-tuning: {trainable_params_after}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/full_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Full fine-tuning the model.")
    fine_tuned_model, fine_tuned_memory_increase, avg_epoch_time, trainable_params_after = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'full_fine_tuned_model_additional_gpu_memory_mb': fine_tuned_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_fine_tuning': trainable_params_before,
        'trainable_parameters_after_fine_tuning': trainable_params_after,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for Full Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/full_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function 

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

Original mBART model GPU memory usage: 2331.27 MB
Trainable parameters before fine-tuning: 610879488
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

Epoch 5.0 took 934.05 seconds


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 200, 'early_stopping': True, 'num_beams': 5, 'forced_eos_token_id': 2}
There were missing keys in the checkpoint model loaded: ['model.encoder.embed_tokens.weight', 'model.decoder.embed_tokens.weight', 'lm_head.weight'].
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 200, 'early_stopping': True, 'num_beams': 5, 'forced_eos_token_id': 2}


Full fine-tuned model additional GPU memory usage after training: 4676.89 MB
Trainable parameters after full fine-tuning: 610879488
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/full_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [10:29<00:00,  2.42it/s]


Summary of Results for Full Fine-tuned mBART:
         original_model_gpu_memory_mb  full_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_fine_tuning  trainable_parameters_after_fine_tuning
Overall                   2331.274414                                     4676.891602                       887.557712                0.404523      0.823913    0.762182                                610879488                               610879488
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/full_fine_tuned_mbart_performance.csv


LoRA model Evaluation

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import MBartForConditionalGeneration, MBartTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
import nltk
import torch
import gc
import time
from tqdm import tqdm
from collections import defaultdict
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download NLTK data
nltk.download('punkt_tab')
nltk.download('wordnet')

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    start_time = time.time()
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=max_length, forced_bos_token_id=forced_bos_token_id)
    end_time = time.time()

    translation = tokenizer.batch_decode(outputs, skip_special_tokens=True)[0]
    return translation, end_time - start_time

def calculate_metrics(reference, candidate):
    ref_tokens = nltk.word_tokenize(reference.lower())
    cand_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([ref_tokens], cand_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

def process_csv_files(root_dir):
    results = {}
    for primary_category in os.listdir(root_dir):
        primary_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_path):
            results[primary_category] = {}
            for sentence_type in os.listdir(primary_path):
                sentence_path = os.path.join(primary_path, sentence_type)
                if os.path.isdir(sentence_path):
                    results[primary_category][sentence_type] = {}
                    for file in os.listdir(sentence_path):
                        if file.endswith(".csv"):
                            tense = file[:-4]
                            file_path = os.path.join(sentence_path, file)
                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))
                            results[primary_category][sentence_type][tense] = data
    return results

def aggregate_results(results, model_name, memory_usage_mb, avg_inference_time):
    rows = []
    for primary_category, types in results.items():
        for sentence_type, tenses in types.items():
            for tense, data in tenses.items():
                rows.append({
                    'primary_category': primary_category,
                    'sentence_type': sentence_type,
                    'tense': tense,
                    'meteor': data['scores']['meteor'],
                    'chrf': data['scores']['chrf']
                })

    df = pd.DataFrame(rows)
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    global_stats = df[score_columns].mean().to_dict()
    global_stats['model_gpu_memory_MB'] = memory_usage_mb
    global_stats['avg_inference_time_sec'] = avg_inference_time

    out_path = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/{model_name}_metrics.csv'
    df.to_csv(out_path, index=False)
    print(f"\nSaved detailed results to {out_path}")

    print("\n--- Overall Evaluation Summary ---")
    for k, v in global_stats.items():
        print(f"{k}: {v:.4f}" if isinstance(v, float) else f"{k}: {v}")
    return df, global_stats

def main():
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    torch.cuda.empty_cache()
    torch.cuda.reset_peak_memory_stats()

    model_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3"
    model = MBartForConditionalGeneration.from_pretrained(model_dir)
    model.to(device)

    torch.cuda.synchronize()
    time.sleep(2)
    peak_memory = torch.cuda.max_memory_allocated() / (1024 * 1024)

    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    results = {}
    all_inference_times = []

    for pc, types in test_data.items():
        results[pc] = {}
        for st, tenses in types.items():
            results[pc][st] = {}
            for tense, data in tenses.items():
                print(f"Evaluating: {pc} - {st} - {tense}")
                try:
                    metrics = evaluate_model(model, tokenizer, data)
                    results[pc][st][tense] = {'scores': {
                        'meteor': metrics['meteor'],
                        'chrf': metrics['chrf']
                    }}
                    all_inference_times.append(metrics['avg_inference_time'])
                except Exception as e:
                    print(f"Error: {e}")
                    results[pc][st][tense] = {'scores': {'meteor': 0.0, 'chrf': 0.0}}
                clear_gpu_memory()

    avg_inference_time = np.mean(all_inference_times)
    aggregate_results(results, "fine_tuned_mbart", peak_memory, avg_inference_time)

if __name__ == "__main__":
    main()

Mounted at /content/drive


[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

...

Evaluating: Voice and Speech Constructions - Active Voice - simple_past


100%|██████████| 15/15 [00:03<00:00,  4.26it/s]


Evaluating: Voice and Speech Constructions - Active Voice - simple_present


100%|██████████| 15/15 [00:03<00:00,  3.93it/s]



Saved detailed results to /content/drive/MyDrive/Colab Notebooks/Translation Models/results/fine_tuned_mbart_metrics.csv

--- Overall Evaluation Summary ---
meteor: 0.8065
chrf: 0.7387
model_gpu_memory_MB: 2340.2744
avg_inference_time_sec: 0.3339


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "हम भोजन कर रहे होंगे!",
    "क्या तुमने खाना खा लिया था?",
    "वह उल्टा चोर कोतवाल को डाँट रहा था!",
    "उसे ऊँची दुकान फीका पकवान मिला!",
    "क्या वैज्ञानिकों ने नई खोज की है?",
    "टीम नई सुविधाओं का परीक्षण करती है।"
]

print("LoRA Best mBART model's translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Mounted at /content/drive


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/649 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.43k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


model.safetensors:   0%|          | 0.00/2.44G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

LoRA Best mBART model's translations:
Original: हम भोजन कर रहे होंगे!
Translated: We will be having lunch!
Original: क्या तुमने खाना खा लिया था?
Translated: Had you eaten the food?
Original: वह उल्टा चोर कोतवाल को डाँट रहा था!
Translated: He was blaming others!
Original: उसे ऊँची दुकान फीका पकवान मिला!
Translated: He found the high-profile shop delicious!
Original: क्या वैज्ञानिकों ने नई खोज की है?
Translated: Have scientists made a new discovery?
Original: टीम नई सुविधाओं का परीक्षण करती है।
Translated: The team tests new features.


QLoRA model evaluation

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import MBartForConditionalGeneration, MBartTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
import nltk
import torch
import gc
import time
from tqdm import tqdm
from collections import defaultdict
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download NLTK data
nltk.download('punkt_tab')
nltk.download('wordnet')

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    start_time = time.time()
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=max_length, forced_bos_token_id=forced_bos_token_id)
    end_time = time.time()

    translation = tokenizer.batch_decode(outputs, skip_special_tokens=True)[0]
    return translation, end_time - start_time

def calculate_metrics(reference, candidate):
    ref_tokens = nltk.word_tokenize(reference.lower())
    cand_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([ref_tokens], cand_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

def process_csv_files(root_dir):
    results = {}
    for primary_category in os.listdir(root_dir):
        primary_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_path):
            results[primary_category] = {}
            for sentence_type in os.listdir(primary_path):
                sentence_path = os.path.join(primary_path, sentence_type)
                if os.path.isdir(sentence_path):
                    results[primary_category][sentence_type] = {}
                    for file in os.listdir(sentence_path):
                        if file.endswith(".csv"):
                            tense = file[:-4]
                            file_path = os.path.join(sentence_path, file)
                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))
                            results[primary_category][sentence_type][tense] = data
    return results

def aggregate_results(results, model_name, memory_usage_mb, avg_inference_time):
    rows = []
    for primary_category, types in results.items():
        for sentence_type, tenses in types.items():
            for tense, data in tenses.items():
                rows.append({
                    'primary_category': primary_category,
                    'sentence_type': sentence_type,
                    'tense': tense,
                    'meteor': data['scores']['meteor'],
                    'chrf': data['scores']['chrf']
                })

    df = pd.DataFrame(rows)
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    global_stats = df[score_columns].mean().to_dict()
    global_stats['model_gpu_memory_MB'] = memory_usage_mb
    global_stats['avg_inference_time_sec'] = avg_inference_time

    out_path = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/{model_name}_metrics.csv'
    df.to_csv(out_path, index=False)
    print(f"\nSaved detailed results to {out_path}")

    print("\n--- Overall Evaluation Summary ---")
    for k, v in global_stats.items():
        print(f"{k}: {v:.4f}" if isinstance(v, float) else f"{k}: {v}")
    return df, global_stats

def main():
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    torch.cuda.empty_cache()
    torch.cuda.reset_peak_memory_stats()

    model_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model = MBartForConditionalGeneration.from_pretrained(model_dir)
    model.to(device)

    torch.cuda.synchronize()
    time.sleep(2)
    peak_memory = torch.cuda.max_memory_allocated() / (1024 * 1024)

    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    results = {}
    all_inference_times = []

    for pc, types in test_data.items():
        results[pc] = {}
        for st, tenses in types.items():
            results[pc][st] = {}
            for tense, data in tenses.items():
                print(f"Evaluating: {pc} - {st} - {tense}")
                try:
                    metrics = evaluate_model(model, tokenizer, data)
                    results[pc][st][tense] = {'scores': {
                        'meteor': metrics['meteor'],
                        'chrf': metrics['chrf']
                    }}
                    all_inference_times.append(metrics['avg_inference_time'])
                except Exception as e:
                    print(f"Error: {e}")
                    results[pc][st][tense] = {'scores': {'meteor': 0.0, 'chrf': 0.0}}
                clear_gpu_memory()

    avg_inference_time = np.mean(all_inference_times)
    aggregate_results(results, "fine_tuned_mbart", peak_memory, avg_inference_time)

if __name__ == "__main__":
    main()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Using device: cuda


[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Evaluating: Standard Sentences - Exclamatory Sentences - past_perfect


100%|██████████| 8/8 [00:02<00:00,  3.59it/s]


Evaluating: Standard Sentences - Exclamatory Sentences - present_perfect


...

Evaluating: Voice and Speech Constructions - Active Voice - simple_past


100%|██████████| 15/15 [00:03<00:00,  4.32it/s]


Evaluating: Voice and Speech Constructions - Active Voice - simple_present


100%|██████████| 15/15 [00:04<00:00,  3.56it/s]



Saved detailed results to /content/drive/MyDrive/Colab Notebooks/Translation Models/results/fine_tuned_mbart_metrics.csv

--- Overall Evaluation Summary ---
meteor: 0.7845
chrf: 0.7215
model_gpu_memory_MB: 2348.3994
avg_inference_time_sec: 0.3276


In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import MBartForConditionalGeneration, MBartTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
import nltk
import torch
import gc
import time
from tqdm import tqdm
from collections import defaultdict
from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Download NLTK data
nltk.download('punkt_tab')
nltk.download('wordnet')

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    start_time = time.time()
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=max_length, forced_bos_token_id=forced_bos_token_id)
    end_time = time.time()

    translation = tokenizer.batch_decode(outputs, skip_special_tokens=True)[0]
    return translation, end_time - start_time

def calculate_metrics(reference, candidate):
    ref_tokens = nltk.word_tokenize(reference.lower())
    cand_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([ref_tokens], cand_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

def process_csv_files(root_dir):
    results = {}
    for primary_category in os.listdir(root_dir):
        primary_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_path):
            results[primary_category] = {}
            for sentence_type in os.listdir(primary_path):
                sentence_path = os.path.join(primary_path, sentence_type)
                if os.path.isdir(sentence_path):
                    results[primary_category][sentence_type] = {}
                    for file in os.listdir(sentence_path):
                        if file.endswith(".csv"):
                            tense = file[:-4]
                            file_path = os.path.join(sentence_path, file)
                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))
                            results[primary_category][sentence_type][tense] = data
    return results

def aggregate_results(results, model_name, memory_usage_mb, avg_inference_time):
    rows = []
    for primary_category, types in results.items():
        for sentence_type, tenses in types.items():
            for tense, data in tenses.items():
                rows.append({
                    'primary_category': primary_category,
                    'sentence_type': sentence_type,
                    'tense': tense,
                    'meteor': data['scores']['meteor'],
                    'chrf': data['scores']['chrf']
                })

    df = pd.DataFrame(rows)
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    global_stats = df[score_columns].mean().to_dict()
    global_stats['model_gpu_memory_MB'] = memory_usage_mb
    global_stats['avg_inference_time_sec'] = avg_inference_time

    out_path = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/{model_name}_metrics.csv'
    df.to_csv(out_path, index=False)
    print(f"\nSaved detailed results to {out_path}")

    print("\n--- Overall Evaluation Summary ---")
    for k, v in global_stats.items():
        print(f"{k}: {v:.4f}" if isinstance(v, float) else f"{k}: {v}")
    return df, global_stats

def main():
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    torch.cuda.empty_cache()
    torch.cuda.reset_peak_memory_stats()

    model_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=True
    )

    # Set group size through environment variable
    import os
    os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_dir,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )


    torch.cuda.synchronize()
    time.sleep(2)
    peak_memory = torch.cuda.max_memory_allocated() / (1024 * 1024)

    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)/test_set')

    results = {}
    all_inference_times = []

    for pc, types in test_data.items():
        results[pc] = {}
        for st, tenses in types.items():
            results[pc][st] = {}
            for tense, data in tenses.items():
                print(f"Evaluating: {pc} - {st} - {tense}")
                try:
                    metrics = evaluate_model(model, tokenizer, data)
                    results[pc][st][tense] = {'scores': {
                        'meteor': metrics['meteor'],
                        'chrf': metrics['chrf']
                    }}
                    all_inference_times.append(metrics['avg_inference_time'])
                except Exception as e:
                    print(f"Error: {e}")
                    results[pc][st][tense] = {'scores': {'meteor': 0.0, 'chrf': 0.0}}
                clear_gpu_memory()

    avg_inference_time = np.mean(all_inference_times)
    aggregate_results(results, "fine_tuned_mbart", peak_memory, avg_inference_time)

if __name__ == "__main__":
    main()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

...

Evaluating: Voice and Speech Constructions - Active Voice - simple_past


100%|██████████| 15/15 [00:07<00:00,  2.14it/s]


Evaluating: Voice and Speech Constructions - Active Voice - simple_present


100%|██████████| 15/15 [00:06<00:00,  2.20it/s]



Saved detailed results to /content/drive/MyDrive/Colab Notebooks/Translation Models/results/fine_tuned_mbart_metrics.csv

--- Overall Evaluation Summary ---
meteor: 0.7835
chrf: 0.7209
model_gpu_memory_MB: 1643.9819
avg_inference_time_sec: 0.5991


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "हम भोजन कर रहे होंगे!",
    "क्या तुमने खाना खा लिया था?",
    "वह उल्टा चोर कोतवाल को डाँट रहा था!",
    "उसे ऊँची दुकान फीका पकवान मिला!",
    "क्या वैज्ञानिकों ने नई खोज की है?",
    "टीम नई सुविधाओं का परीक्षण करती है।"
]

print("QLoRA Best mBART model's translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
LoRA Best mBART model's translations:
Original: हम भोजन कर रहे होंगे!
Translated: We will be eating!
Original: क्या तुमने खाना खा लिया था?
Translated: Had you eaten the food?
Original: वह उल्टा चोर कोतवाल को डाँट रहा था!
Translated: The thief was scoffing at the opportunity!
Original: उसे ऊँची दुकान फीका पकवान मिला!
Translated: He got a flattened dish from the high store!
Original: क्या वैज्ञानिकों ने नई खोज की है?
Translated: What have scientists discovered newly?
Original: टीम नई सुविधाओं का परीक्षण करती है।
Translated: The team tests new features.


## **LoRA fine-tuning**

### Rank Optimization

#### r=2, alpha=32, dropout=0.1

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=2,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Original mBART model GPU memory usage: 2331.27 MB
Trainable parameters before LoRA: 610879488
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 283.77 seconds
Epoch 2.0 took 284.18 seconds
Epoch 3.0 took 285.71 seconds
Epoch 4.0 took 285.21 seconds
Epoch 5.0 took 313.04 seconds
LoRA fine-tuned model additional GPU memory usage after training: 5.06 MB
Trainable parameters after training: 442368
LoRA parameters after training: 442368
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [11:04<00:00,  2.29it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                        5.063477                       290.381519                0.423062      0.797991    0.731901                         610879488                           442368           442368
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### r= 12

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=12,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Original mBART model GPU memory usage: 2331.27 MB
Trainable parameters before LoRA: 610879488
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 289.10 seconds
Epoch 2.0 took 286.79 seconds
Epoch 3.0 took 284.51 seconds
Epoch 4.0 took 285.23 seconds
Epoch 5.0 took 304.69 seconds
LoRA fine-tuned model additional GPU memory usage after training: 30.38 MB
Trainable parameters after training: 2654208
LoRA parameters after training: 2654208
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [11:04<00:00,  2.29it/s]


Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       30.375977                       290.063872                0.423635      0.796202    0.733117                         610879488                          2654208          2654208
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### r=16 (BEST)

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization3"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 291.52 seconds
Epoch 2.0 took 291.33 seconds
Epoch 3.0 took 291.65 seconds
Epoch 4.0 took 291.56 seconds
Epoch 5.0 took 291.66 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization3
Evaluating the model.


100%|██████████| 1523/1523 [11:57<00:00,  2.12it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       291.543464                0.456995       0.80167     0.73569                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### r=48

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=48,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Original mBART model GPU memory usage: 2331.27 MB
Trainable parameters before LoRA: 610879488
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 300.43 seconds
Epoch 2.0 took 312.19 seconds
Epoch 3.0 took 301.99 seconds
Epoch 4.0 took 295.41 seconds
Epoch 5.0 took 318.14 seconds
LoRA fine-tuned model additional GPU memory usage after training: 137.75 MB
Trainable parameters after training: 10616832
LoRA parameters after training: 10616832
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization4
Evaluating the model.


100%|██████████| 1523/1523 [10:53<00:00,  2.33it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                      137.750977                       305.629225                0.415606      0.799463    0.733539                         610879488                         10616832         10616832
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### r=64

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=64,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model("/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization4", peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Original mBART model GPU memory usage: 2331.27 MB
Trainable parameters before LoRA: 610879488
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 298.10 seconds
Epoch 2.0 took 297.87 seconds
Epoch 3.0 took 299.20 seconds
Epoch 4.0 took 298.90 seconds
Epoch 5.0 took 299.19 seconds
LoRA fine-tuned model additional GPU memory usage after training: 192.43 MB
Trainable parameters after training: 14155776
LoRA parameters after training: 14155776
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_rank_optimization4
Evaluating the model.


100%|██████████| 1523/1523 [11:40<00:00,  2.17it/s]


Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                    192.43                      298.650321                0.446267      0.795816    0.730889                         610879488                         14155776         14155776
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


### Alpha Optimization

#### alpha = 8

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=8,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 294.71 seconds
Epoch 2.0 took 293.97 seconds
Epoch 3.0 took 294.36 seconds
Epoch 4.0 took 293.99 seconds
Epoch 5.0 took 295.01 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [10:56<00:00,  2.32it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       294.406381                0.416995      0.785965    0.720382                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### alpha = 32

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=32,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 287.38 seconds
Epoch 2.0 took 287.94 seconds
Epoch 3.0 took 289.08 seconds
Epoch 4.0 took 289.71 seconds
Epoch 5.0 took 289.11 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization2
Evaluating the model.


100%|██████████| 1523/1523 [10:54<00:00,  2.33it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       288.640617                0.416441      0.799623     0.73565                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### alpha = 64

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=64,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization3"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 289.40 seconds
Epoch 2.0 took 288.33 seconds
Epoch 3.0 took 288.12 seconds
Epoch 4.0 took 288.24 seconds
Epoch 5.0 took 288.60 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization3
Evaluating the model.


100%|██████████| 1523/1523 [10:39<00:00,  2.38it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       288.535421                0.406767      0.803014    0.740331                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### alpha = 128

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=128,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 296.87 seconds
Epoch 2.0 took 300.46 seconds
Epoch 3.0 took 300.80 seconds
Epoch 4.0 took 300.56 seconds
Epoch 5.0 took 300.51 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization4
Evaluating the model.


100%|██████████| 1523/1523 [11:01<00:00,  2.30it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       299.840954                0.420509      0.810165    0.748441                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### alpha = 512 (BEST)

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 297.88 seconds
Epoch 2.0 took 296.30 seconds
Epoch 3.0 took 298.18 seconds
Epoch 4.0 took 297.14 seconds
Epoch 5.0 took 297.50 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5
Evaluating the model.


100%|██████████| 1523/1523 [11:23<00:00,  2.23it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       297.397997                0.434374       0.82028    0.758328                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### Alpha Optimization Example Improvements

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import nltk
from collections import defaultdict
import torch
from multiprocessing import Pool
import gc
from google.colab import drive
from transformers import MBartForConditionalGeneration, MBartTokenizer


# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('punkt_tab')

# Check if GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def translate_with_model(texts, model, tokenizer, max_length=100, batch_size=32):
    all_translations = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        # Set source language to Hindi and target language to English
        tokenizer.src_lang = "hi_IN"  # Hindi language code
        tokenizer.tgt_lang = "en_XX"  # English language code

        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

        # Force the model to translate to English
        forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

        with torch.no_grad():
            translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

        batch_translations = tokenizer.batch_decode(translated, skip_special_tokens=True)
        all_translations.extend(batch_translations)
    return all_translations

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())

    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100

    return {
        'meteor': meteor,
        'chrf': chrf_score
    }

def calculate_metrics_wrapper(args):
    reference, candidate = args
    return calculate_metrics(reference, candidate)

def evaluate_model(model, tokenizer, test_data, model_name):
    all_scores = defaultdict(list)
    all_translations = []

    print(f"\nEvaluating {model_name}:")
    hindi_texts, english_texts = zip(*test_data)

    translations = translate_with_model(hindi_texts, model, tokenizer)

    # Use multiprocessing for metric calculation
    with Pool() as pool:
        scores_list = pool.map(calculate_metrics_wrapper, zip(english_texts, translations))

    for hindi, english, translation, scores in zip(hindi_texts, english_texts, translations, scores_list):
        for metric, score in scores.items():
            all_scores[metric].append(score)

        all_translations.append({
            'hindi': hindi,
            'english_reference': english,
            'english_translation': translation,
            'scores': scores
        })

    return all_scores, all_translations

def process_csv_files(root_dir):
    results = {}

    for primary_category in os.listdir(root_dir):
        primary_category_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_category_path):
            results[primary_category] = {}

            for sentence_type in os.listdir(primary_category_path):
                sentence_type_path = os.path.join(primary_category_path, sentence_type)
                if os.path.isdir(sentence_type_path):
                    results[primary_category][sentence_type] = {}

                    for file in os.listdir(sentence_type_path):
                        if file.endswith('.csv'):
                            tense = os.path.splitext(file)[0]
                            file_path = os.path.join(sentence_type_path, file)

                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))

                            results[primary_category][sentence_type][tense] = data

    return results

def aggregate_results(results, model_name):
    aggregated = {
        'primary_category': [],
        'sentence_type': [],
        'tense': [],
        'meteor': [],
        'chrf': []
    }

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                aggregated['primary_category'].append(primary_category)
                aggregated['sentence_type'].append(sentence_type)
                aggregated['tense'].append(tense)
                for metric in ['meteor', 'chrf']:
                    aggregated[metric].append(np.mean([translation['scores'][metric] for translation in data['translations']]))

    df = pd.DataFrame(aggregated)

    # Convert score columns to numeric, coercing errors to NaN
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    # Global performance for each primary category
    global_primary = df.groupby('primary_category')[score_columns].mean().reset_index()
    global_primary['category'] = 'Global Primary Category'

    # Global performance for each sentence type
    global_sentence_type = df.groupby('sentence_type')[score_columns].mean().reset_index()
    global_sentence_type['category'] = 'Global Sentence Type'

    # Global performance for each tense
    global_tense = df.groupby('tense')[score_columns].mean().reset_index()
    global_tense['category'] = 'Global Tense'

    # Combine all results
    all_results = pd.concat([df, global_primary, global_sentence_type, global_tense], sort=False)
    print(all_results)

    # Save results to CSV in Google Drive
    csv_filename = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/basemodel_performance.csv'
    all_results.to_csv(csv_filename, index=False)
    print(f"Results for {model_name} have been saved to '{csv_filename}'")

    return all_results

def get_worst_performers(results, n=6):
    worst_performers = defaultdict(lambda: defaultdict(list))

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                for translation in data['translations']:
                    for metric, score in translation['scores'].items():
                        worst_performers[primary_category][metric].append((score, translation))

    for primary_category in worst_performers:
        for metric in worst_performers[primary_category]:
            worst_performers[primary_category][metric].sort(key=lambda x: x[0])
            worst_performers[primary_category][metric] = worst_performers[primary_category][metric][:n]

    return worst_performers

def print_worst_performers(worst_performers, model_name):
    print(f"\n--- Worst Performers for {model_name} ---")
    for primary_category, metrics in worst_performers.items():
        print(f"\nPrimary Category: {primary_category}")
        for metric, performers in metrics.items():
            print(f"\n  Metric: {metric}")
            for i, (score, translation) in enumerate(performers, 1):
                print(f"    {i}. Score: {score:.4f}")
                print(f"       Hindi Text: {translation['hindi']}")
                print(f"       English Reference: {translation['english_reference']}")
                print(f"       Model Translation: {translation['english_translation']}")

def main():
    # Load models
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"
    tokenizer = MBartTokenizer.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
    model = MBartForConditionalGeneration.from_pretrained("/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization1")
    model.to(device)

    # Process CSV files from Google Drive
    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted/test_set')

    # Evaluate models
    marianmt_results = {}

    for primary_category, sentence_types in test_data.items():
        marianmt_results[primary_category] = {}
        for sentence_type, tenses in sentence_types.items():
            print(f"Evaluating {primary_category} - {sentence_type}")
            marianmt_results[primary_category][sentence_type] = {}
            for tense, data in tenses.items():
                print(f"Evaluating {primary_category} - {sentence_type} - {tense}")
                try:
                    marianmt_scores, marianmt_translations = evaluate_model(model, tokenizer, data, "mBART")

                    marianmt_results[primary_category][sentence_type][tense] = {
                        'scores': marianmt_scores,
                        'translations': marianmt_translations
                    }
                except Exception as e:
                    print(f"Error processing {primary_category} - {sentence_type} - {tense}: {str(e)}")
                    marianmt_results[primary_category][sentence_type][tense] = {'error': str(e)}

                # Clear GPU memory after processing each tense
                clear_gpu_memory()

    # Get worst performers
    marianmt_worst = get_worst_performers(marianmt_results)

    # Print worst performers
    print_worst_performers(marianmt_worst, "mBART")

    # Aggregate and save results
    marianmt_all_results = aggregate_results(marianmt_results, "mBART")

    # Print summary
    for model_name, results in [("MarianMT", marianmt_all_results)]:
        print(f"\nSummary of Results for {model_name}:")
        for category in ['Global Primary Category', 'Global Sentence Type', 'Global Tense']:
            print(f"\n{category} Performance:")
            summary = results[results['category'] == category]
            mean_scores = summary[['meteor', 'chrf']].mean()
            print(mean_scores)

if __name__ == "__main__":
    main()

Mounted at /content/drive


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


Using device: cuda


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

...

config.json:   0%|          | 0.00/1.43k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


model.safetensors:   0%|          | 0.00/2.44G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

Evaluating Standard Sentences - Exclamatory Sentences
Evaluating Standard Sentences - Exclamatory Sentences - past_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - past_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_present

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_past

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_future

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_continuous

Evaluating mBART:
Evaluating Standard Sentences - Declarative Sentences
Evaluating Standard Sentences - Declarative Sentences - past_continuous

Evalua

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization2"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "क्या अद्भुत सवारी होगी!",
    "जिम जाओ।",
    "वह उम्र भर का साथ निभा रहा था।",
    "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
    "वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।",
    "मुद्दों पर बहस की जा रही होगी।"
]

print("full fine-tuned mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Mounted at /content/drive


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/649 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.43k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


model.safetensors:   0%|          | 0.00/2.44G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

full fine-tuned mBART translations:
Original: क्या अद्भुत सवारी होगी!
Translated: What a wonderful ride it will be!
Original: जिम जाओ।
Translated: Go to the gym.
Original: वह उम्र भर का साथ निभा रहा था।
Translated: He was enjoying lifelong companionship.
Original: उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।
Translated: He worked so hard that neither the snake died nor the staff broke.
Original: वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।
Translated: He is saying that the president faces a tough challenge in the election.
Original: मुद्दों पर बहस की जा रही होगी।
Translated: Issues will be under discussion.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization3"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "क्या अद्भुत सवारी होगी!",
    "जिम जाओ।",
    "वह उम्र भर का साथ निभा रहा था।",
    "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
    "वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।",
    "मुद्दों पर बहस की जा रही होगी।"
]

print("alpha=64 mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


alpha=64 mBART translations:
Original: क्या अद्भुत सवारी होगी!
Translated: What a wonderful ride it will be!
Original: जिम जाओ।
Translated: Go to the gym.
Original: वह उम्र भर का साथ निभा रहा था।
Translated: He was enjoying lifelong friendships.
Original: उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।
Translated: He worked in such a way that neither the snake died nor the rod broke.
Original: वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।
Translated: He is saying that the president faces tough challenges in the election.
Original: मुद्दों पर बहस की जा रही होगी।
Translated: Issues will be under discussion.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization4"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "क्या अद्भुत सवारी होगी!",
    "जिम जाओ।",
    "वह उम्र भर का साथ निभा रहा था।",
    "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
    "वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।",
    "मुद्दों पर बहस की जा रही होगी।"
]

print("alpha=128 mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
alpha=128 mBART translations:
Original: क्या अद्भुत सवारी होगी!
Translated: What a wonderful ride it will be!
Original: जिम जाओ।
Translated: Go to gym.
Original: वह उम्र भर का साथ निभा रहा था।
Translated: He was playing along for life.
Original: उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।
Translated: He worked so hard that the snake died and the staff didn't break.
Original: वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।
Translated: He is saying that the presidential election is facing tough challenges.
Original: मुद्दों पर बहस की जा रही होगी।
Translated: The issues will be being discussed.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "क्या अद्भुत सवारी होगी!",
    "जिम जाओ।",
    "वह उम्र भर का साथ निभा रहा था।",
    "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
    "वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।",
    "मुद्दों पर बहस की जा रही होगी।"
]

print("alpha=512 mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
alpha=512 mBART translations:
Original: क्या अद्भुत सवारी होगी!
Translated: What a wonderful ride it will be!
Original: जिम जाओ।
Translated: Go to the gym.
Original: वह उम्र भर का साथ निभा रहा था।
Translated: He was serving a lifelong friendship.
Original: उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।
Translated: He worked in such a way that even the snake died and the staff broke off.
Original: वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।
Translated: He is saying that there is a fierce struggle in the presidential election.
Original: मुद्दों पर बहस की जा रही होगी।
Translated: The issues will be being discussed.


### Dropout Optimization

#### dropout = 0.0 (BEST)

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 281.46 seconds
Epoch 2.0 took 279.48 seconds
Epoch 3.0 took 279.47 seconds
Epoch 4.0 took 278.80 seconds
Epoch 5.0 took 279.13 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [10:40<00:00,  2.38it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       279.666223                0.407156      0.827864    0.770722                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### dropout = 0.1

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.1,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 297.88 seconds
Epoch 2.0 took 296.30 seconds
Epoch 3.0 took 298.18 seconds
Epoch 4.0 took 297.14 seconds
Epoch 5.0 took 297.50 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5
Evaluating the model.


100%|██████████| 1523/1523 [11:23<00:00,  2.23it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       297.397997                0.434374       0.82028    0.758328                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### dropout = 0.2

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.2,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 294.97 seconds
Epoch 2.0 took 301.43 seconds
Epoch 3.0 took 302.21 seconds
Epoch 4.0 took 302.58 seconds
Epoch 5.0 took 302.36 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization2
Evaluating the model.


100%|██████████| 1523/1523 [11:02<00:00,  2.30it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       300.711228                0.420961      0.826811    0.768997                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### dropout = 0.3

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.3,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization3"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 287.51 seconds
Epoch 2.0 took 285.23 seconds


Epoch 3.0 took 285.98 seconds
Epoch 4.0 took 285.81 seconds
Epoch 5.0 took 286.86 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization3
Evaluating the model.


100%|██████████| 1523/1523 [10:46<00:00,  2.35it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       286.276479                 0.41085      0.825085    0.765697                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### dropout = 0.5

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.5,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 297.47 seconds
Epoch 2.0 took 298.99 seconds
Epoch 3.0 took 299.16 seconds
Epoch 4.0 took 298.43 seconds
Epoch 5.0 took 299.35 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization4
Evaluating the model.


100%|██████████| 1523/1523 [10:54<00:00,  2.33it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       298.679385                 0.41721      0.823504    0.765586                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


### Target Module Optimization

#### module = ["q_proj", "v_proj"]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["q_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 261.76 seconds
Epoch 2.0 took 264.83 seconds
Epoch 3.0 took 265.50 seconds
Epoch 4.0 took 265.56 seconds
Epoch 5.0 took 265.80 seconds
LoRA fine-tuned model additional GPU memory usage after training: 43.25 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [11:43<00:00,  2.17it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       43.250977                       264.689113                0.449726      0.772453    0.706237                         610879488                          2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### module = ["q_proj", "k_proj", "v_proj", "o_proj"]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["q_proj", "v_proj", "k_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 281.46 seconds
Epoch 2.0 took 279.48 seconds
Epoch 3.0 took 279.47 seconds
Epoch 4.0 took 278.80 seconds
Epoch 5.0 took 279.13 seconds
LoRA fine-tuned model additional GPU memory usage after training: 56.75 MB
Trainable parameters after training: 3538944
LoRA parameters after training: 3538944
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_dropout_optimization1
Evaluating the model.


100%|██████████| 1523/1523 [10:40<00:00,  2.38it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       56.750977                       279.666223                0.407156      0.827864    0.770722                         610879488                          3538944          3538944
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### module = ["k_proj", "v_proj"] (BEST)

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 267.38 seconds
Epoch 2.0 took 265.30 seconds
Epoch 3.0 took 265.69 seconds
Epoch 4.0 took 266.06 seconds
Epoch 5.0 took 266.32 seconds
LoRA fine-tuned model additional GPU memory usage after training: 43.25 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3
Evaluating the model.


100%|██████████| 1523/1523 [09:45<00:00,  2.60it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       43.250977                       266.148165                0.371534       0.82963     0.77072                         610879488                          2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "हम भोजन कर रहे होंगे!",
    "क्या तुमने खाना खा लिया था?",
    "वह उल्टा चोर कोतवाल को डाँट रहा था!",
    "उसे ऊँची दुकान फीका पकवान मिला!",
    "क्या वैज्ञानिकों ने नई खोज की है?",
    "टीम नई सुविधाओं का परीक्षण करती है।"
]

print("['k_proj', 'v_proj'] mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Mounted at /content/drive


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/649 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.43k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


model.safetensors:   0%|          | 0.00/2.44G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

['k_proj', 'v_proj'] mBART translations:
Original: हम भोजन कर रहे होंगे!
Translated: We will be having lunch!
Original: क्या तुमने खाना खा लिया था?
Translated: Had you eaten the food?
Original: वह उल्टा चोर कोतवाल को डाँट रहा था!
Translated: He was blaming others!
Original: उसे ऊँची दुकान फीका पकवान मिला!
Translated: He found the high-profile shop delicious!
Original: क्या वैज्ञानिकों ने नई खोज की है?
Translated: Have scientists made a new discovery?
Original: टीम नई सुविधाओं का परीक्षण करती है।
Translated: The team tests new features.


#### module = ["q_proj", "k_proj"]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["q_proj", "k_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 280.60 seconds
Epoch 2.0 took 278.35 seconds
Epoch 3.0 took 277.95 seconds
Epoch 4.0 took 277.50 seconds
Epoch 5.0 took 277.93 seconds
LoRA fine-tuned model additional GPU memory usage after training: 43.25 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization2
Evaluating the model.


100%|██████████| 1523/1523 [10:01<00:00,  2.53it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       43.250977                       278.466149                0.382232      0.797757    0.734915                         610879488                          2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### module = ["v_proj", "o_proj"]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["v_proj", "o_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization5"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with LoRA.


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 248.64 seconds
Epoch 2.0 took 245.76 seconds
Epoch 3.0 took 245.57 seconds
Epoch 4.0 took 245.46 seconds
Epoch 5.0 took 247.18 seconds
LoRA fine-tuned model additional GPU memory usage after training: 29.75 MB
Trainable parameters after training: 1179648
LoRA parameters after training: 1179648
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization4
Evaluating the model.


100%|██████████| 1523/1523 [18:21<00:00,  1.38it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                       29.750977                       246.522513                 0.71201      0.714973    0.648955                         610879488                          1179648          1179648
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### module = ["q_proj", "k_proj", "v_proj", "o_proj", "fc1", "fc2"]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    """Count the number of trainable parameters in the model."""
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    """Count the number of parameters in LoRA layers."""
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before LoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["q_proj", "k_proj", "v_proj", "o_proj", "fc1", "fc2"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Count parameters after training
    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    if trainable_params_after != lora_params:
        print("Warning: The number of trainable parameters doesn't match the number of LoRA parameters.")
        print("This might indicate that some non-LoRA parameters were trained.")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization6"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time, trainable_params_after, lora_params

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time, trainable_params_after, lora_params = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'trainable_parameters_before_lora': trainable_params_before,
        'trainable_parameters_after_lora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for LoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 1.0 took 320.84 seconds


Epoch 2.0 took 318.84 seconds
Epoch 3.0 took 317.81 seconds
Epoch 4.0 took 318.04 seconds
Epoch 5.0 took 319.23 seconds
LoRA fine-tuned model additional GPU memory usage after training: 101.75 MB
Trainable parameters after training: 7471104
LoRA parameters after training: 7471104
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization5
Evaluating the model.


100%|██████████| 1523/1523 [12:12<00:00,  2.08it/s]



Summary of Results for LoRA Fine-tuned mBART:
         original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  avg_inference_time_sec  meteor_score  chrf_score  trainable_parameters_before_lora  trainable_parameters_after_lora  lora_parameters
Overall                   2331.274414                                      101.750977                       318.951714                0.464986      0.829751    0.771007                         610879488                          7471104          7471104
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_performance.csv


#### Target Module Optimization Example Improvements

In [ ]:
import os
import pandas as pd
import numpy as np
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import nltk
from collections import defaultdict
import torch
from multiprocessing import Pool
import gc
from google.colab import drive
from transformers import MBartForConditionalGeneration, MBartTokenizer


# Mount Google Drive
drive.mount('/content/drive')

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('punkt_tab')

# Check if GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def clear_gpu_memory():
    gc.collect()
    torch.cuda.empty_cache()

def translate_with_model(texts, model, tokenizer, max_length=100, batch_size=32):
    all_translations = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        # Set source language to Hindi and target language to English
        tokenizer.src_lang = "hi_IN"  # Hindi language code
        tokenizer.tgt_lang = "en_XX"  # English language code

        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

        # Force the model to translate to English
        forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

        with torch.no_grad():
            translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

        batch_translations = tokenizer.batch_decode(translated, skip_special_tokens=True)
        all_translations.extend(batch_translations)
    return all_translations

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())

    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100

    return {
        'meteor': meteor,
        'chrf': chrf_score
    }

def calculate_metrics_wrapper(args):
    reference, candidate = args
    return calculate_metrics(reference, candidate)

def evaluate_model(model, tokenizer, test_data, model_name):
    all_scores = defaultdict(list)
    all_translations = []

    print(f"\nEvaluating {model_name}:")
    hindi_texts, english_texts = zip(*test_data)

    translations = translate_with_model(hindi_texts, model, tokenizer)

    # Use multiprocessing for metric calculation
    with Pool() as pool:
        scores_list = pool.map(calculate_metrics_wrapper, zip(english_texts, translations))

    for hindi, english, translation, scores in zip(hindi_texts, english_texts, translations, scores_list):
        for metric, score in scores.items():
            all_scores[metric].append(score)

        all_translations.append({
            'hindi': hindi,
            'english_reference': english,
            'english_translation': translation,
            'scores': scores
        })

    return all_scores, all_translations

def process_csv_files(root_dir):
    results = {}

    for primary_category in os.listdir(root_dir):
        primary_category_path = os.path.join(root_dir, primary_category)
        if os.path.isdir(primary_category_path):
            results[primary_category] = {}

            for sentence_type in os.listdir(primary_category_path):
                sentence_type_path = os.path.join(primary_category_path, sentence_type)
                if os.path.isdir(sentence_type_path):
                    results[primary_category][sentence_type] = {}

                    for file in os.listdir(sentence_type_path):
                        if file.endswith('.csv'):
                            tense = os.path.splitext(file)[0]
                            file_path = os.path.join(sentence_type_path, file)

                            df = pd.read_csv(file_path)
                            data = list(zip(df['Hindi_Text'], df['English_Text']))

                            results[primary_category][sentence_type][tense] = data

    return results

def aggregate_results(results, model_name):
    aggregated = {
        'primary_category': [],
        'sentence_type': [],
        'tense': [],
        'meteor': [],
        'chrf': []
    }

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                aggregated['primary_category'].append(primary_category)
                aggregated['sentence_type'].append(sentence_type)
                aggregated['tense'].append(tense)
                for metric in ['meteor', 'chrf']:
                    aggregated[metric].append(np.mean([translation['scores'][metric] for translation in data['translations']]))

    df = pd.DataFrame(aggregated)

    # Convert score columns to numeric, coercing errors to NaN
    score_columns = ['meteor', 'chrf']
    df[score_columns] = df[score_columns].apply(pd.to_numeric, errors='coerce')

    # Global performance for each primary category
    global_primary = df.groupby('primary_category')[score_columns].mean().reset_index()
    global_primary['category'] = 'Global Primary Category'

    # Global performance for each sentence type
    global_sentence_type = df.groupby('sentence_type')[score_columns].mean().reset_index()
    global_sentence_type['category'] = 'Global Sentence Type'

    # Global performance for each tense
    global_tense = df.groupby('tense')[score_columns].mean().reset_index()
    global_tense['category'] = 'Global Tense'

    # Combine all results
    all_results = pd.concat([df, global_primary, global_sentence_type, global_tense], sort=False)
    print(all_results)

    # Save results to CSV in Google Drive
    csv_filename = f'/content/drive/MyDrive/Colab Notebooks/Translation Models/results/basemodel_performance.csv'
    all_results.to_csv(csv_filename, index=False)
    print(f"Results for {model_name} have been saved to '{csv_filename}'")

    return all_results

def get_worst_performers(results, n=6):
    worst_performers = defaultdict(lambda: defaultdict(list))

    for primary_category, sentence_types in results.items():
        for sentence_type, tenses in sentence_types.items():
            for tense, data in tenses.items():
                for translation in data['translations']:
                    for metric, score in translation['scores'].items():
                        worst_performers[primary_category][metric].append((score, translation))

    for primary_category in worst_performers:
        for metric in worst_performers[primary_category]:
            worst_performers[primary_category][metric].sort(key=lambda x: x[0])
            worst_performers[primary_category][metric] = worst_performers[primary_category][metric][:n]

    return worst_performers

def print_worst_performers(worst_performers, model_name):
    print(f"\n--- Worst Performers for {model_name} ---")
    for primary_category, metrics in worst_performers.items():
        print(f"\nPrimary Category: {primary_category}")
        for metric, performers in metrics.items():
            print(f"\n  Metric: {metric}")
            for i, (score, translation) in enumerate(performers, 1):
                print(f"    {i}. Score: {score:.4f}")
                print(f"       Hindi Text: {translation['hindi']}")
                print(f"       English Reference: {translation['english_reference']}")
                print(f"       Model Translation: {translation['english_translation']}")

def main():
    # Load models
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"
    tokenizer = MBartTokenizer.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
    model = MBartForConditionalGeneration.from_pretrained("/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization1")
    model.to(device)

    # Process CSV files from Google Drive
    test_data = process_csv_files('/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted/test_set')

    # Evaluate models
    marianmt_results = {}

    for primary_category, sentence_types in test_data.items():
        marianmt_results[primary_category] = {}
        for sentence_type, tenses in sentence_types.items():
            print(f"Evaluating {primary_category} - {sentence_type}")
            marianmt_results[primary_category][sentence_type] = {}
            for tense, data in tenses.items():
                print(f"Evaluating {primary_category} - {sentence_type} - {tense}")
                try:
                    marianmt_scores, marianmt_translations = evaluate_model(model, tokenizer, data, "mBART")

                    marianmt_results[primary_category][sentence_type][tense] = {
                        'scores': marianmt_scores,
                        'translations': marianmt_translations
                    }
                except Exception as e:
                    print(f"Error processing {primary_category} - {sentence_type} - {tense}: {str(e)}")
                    marianmt_results[primary_category][sentence_type][tense] = {'error': str(e)}

                # Clear GPU memory after processing each tense
                clear_gpu_memory()

    # Get worst performers
    marianmt_worst = get_worst_performers(marianmt_results)

    # Print worst performers
    print_worst_performers(marianmt_worst, "mBART")

    # Aggregate and save results
    marianmt_all_results = aggregate_results(marianmt_results, "mBART")

    # Print summary
    for model_name, results in [("MarianMT", marianmt_all_results)]:
        print(f"\nSummary of Results for {model_name}:")
        for category in ['Global Primary Category', 'Global Sentence Type', 'Global Tense']:
            print(f"\n{category} Performance:")
            summary = results[results['category'] == category]
            mean_scores = summary[['meteor', 'chrf']].mean()
            print(mean_scores)

if __name__ == "__main__":
    main()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


Using device: cuda


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Evaluating Standard Sentences - Exclamatory Sentences
Evaluating Standard Sentences - Exclamatory Sentences - past_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_perfect

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - past_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_present

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_past

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - simple_future

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - future_continuous

Evaluating mBART:
Evaluating Standard Sentences - Exclamatory Sentences - present_continuous

Evaluating mBART:
Evaluating Standard Sentences - Declarative Sentences
Evaluating Standard Sentences - Declarative Sentences - past_continuous

Evalua

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization2"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['q_proj', 'v_proj'] mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Mounted at /content/drive


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/649 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.43k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


model.safetensors:   0%|          | 0.00/2.44G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/261 [00:00<?, ?B/s]

['q_proj', 'v_proj'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Radha washed her clothes and pressed.
Original: चुटकुले सुनाओ।
Translated: Tell a joke.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don't look out for your own benefit. # (अल्लू सीधा करना)
Original: आप तो ईद का चाँद हो गए!
Translated: You became the moon of Eden!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: He had been saved by a mountaineer.
Original: नेताओं ने मतभेद सुलझाए।
Translated: Leaders resolved the differences.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization2"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['q_proj', 'k_proj', 'v_proj', 'o_proj'] mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
['q_proj', 'k_proj', 'v_proj', 'o_proj'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Radha washed her clothes and pressed.
Original: चुटकुले सुनाओ।
Translated: Tell a joke.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don't look out for your own benefit. # (अल्लू सीधा करना)
Original: आप तो ईद का चाँद हो गए!
Translated: You became the moon of Eden!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: He had been saved by a mountaineer.
Original: नेताओं ने मतभेद सुलझाए।
Translated: Leaders resolved the differences.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['k_proj', 'v_proj'] mBART translations:")
translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
['k_proj', 'v_proj'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Radha washed clothes and did the pressing.
Original: चुटकुले सुनाओ।
Translated: Tell jokes.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don't look out for your own benefit. # (अल्लू सीधा करना)
Original: आप तो ईद का चाँद हो गए!
Translated: You have become a rare sight!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: The mountaineering was rescued.
Original: नेताओं ने मतभेद सुलझाए।
Translated: Leaders resolved the differences.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization4"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['q_proj', 'k_proj'] mBART translations:")

translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
['q_proj', 'k_proj'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Radha washed clothes and did the pressing.
Original: चुटकुले सुनाओ।
Translated: Tell jokes.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don't look out for your own benefit. # (उल्लू सीधा करना)
Original: आप तो ईद का चाँद हो गए!
Translated: You have become the moon of Eden!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: The mountaineer had been rescued.
Original: नेताओं ने मतभेद सुलझाए।
Translated: Leaders resolved the difference.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization5"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['v_proj', 'o_proj'] mBART translations:")

translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
['v_proj', 'o_proj'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Rada had shed clothes and done laundry.
Original: चुटकुले सुनाओ।
Translated: Listen quietly.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don't look around expectatively.
Original: आप तो ईद का चाँद हो गए!
Translated: You became a fig Frost Frost Frost Frost!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: The mountaintop had been saved.
Original: नेताओं ने मतभेद सुलझाए।
Translated: The leaders resolved differences.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization6"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "राधा ने कपड़े धोए और प्रेस किए।",
    "चुटकुले सुनाओ।",
    "कृपया अपना उल्लू सीधा मत करो।",
    "आप तो ईद का चाँद हो गए!",
    "उस पर्वतारोही को बचा लिया गया था।",
    "नेताओं ने मतभेद सुलझाए।"
]

print("['q_proj', 'k_proj', 'v_proj', 'o_proj', 'fc1', 'fc2'] mBART translations:")

translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


['q_proj', 'k_proj', 'v_proj', 'o_proj', 'fc1', 'fc2'] mBART translations:
Original: राधा ने कपड़े धोए और प्रेस किए।
Translated: Radha washed clothes and pressed.
Original: चुटकुले सुनाओ।
Translated: Tell a joke.
Original: कृपया अपना उल्लू सीधा मत करो।
Translated: Please don’t be selfish.
Original: आप तो ईद का चाँद हो गए!
Translated: You have become a rare sight!
Original: उस पर्वतारोही को बचा लिया गया था।
Translated: The mountaineering man had been rescued.
Original: नेताओं ने मतभेद सुलझाए।
Translated: Leaders resolved the differences.


In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
from google.colab import drive
import os

# Mount Google Drive
drive.mount('/content/drive')

# Set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load MarianMT model and tokenizer
model_checkpoint = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')
model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
model.to(device)

# Enable CUDA optimizations
torch.backends.cudnn.benchmark = True

@torch.no_grad()
def translate_text(text, model, tokenizer, max_length=512):
    tokenizer.src_lang = "hi_IN"  # Hindi language code
    tokenizer.tgt_lang = "en_XX"  # English language code

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    forced_bos_token_id = tokenizer.lang_code_to_id["en_XX"]

    translated = model.generate(
                **inputs,
                max_length=max_length,
                forced_bos_token_id=forced_bos_token_id
            )

    return tokenizer.decode(translated[0], skip_special_tokens=True)

def batch_translate(texts, model, tokenizer, batch_size=32, max_length=512):
    results = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
        translated = model.generate(**inputs, max_length=max_length)
        results.extend(tokenizer.batch_decode(translated, skip_special_tokens=True))
    return results

# Example usage
hindi_texts = [
    "हम भोजन कर रहे होंगे!",
    "क्या तुमने खाना खा लिया था?",
    "वह उल्टा चोर कोतवाल को डाँट रहा था!",
    "उसे ऊँची दुकान फीका पकवान मिला!",
    "क्या वैज्ञानिकों ने नई खोज की है?",
    "टीम नई सुविधाओं का परीक्षण करती है।"
]

print("Best mBART QLoRA fine-tuned model's translations:")

translations = batch_translate(hindi_texts, model, tokenizer)
for original, translated in zip(hindi_texts, translations):
    print(f"Original: {original}")
    print(f"Translated: {translated}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Best mBART QLoRA fine-tuned model's translations:
Original: हम भोजन कर रहे होंगे!
Translated: We will be eating!
Original: क्या तुमने खाना खा लिया था?
Translated: Had you eaten the food?
Original: वह उल्टा चोर कोतवाल को डाँट रहा था!
Translated: The thief was blaming the thief!
Original: उसे ऊँची दुकान फीका पकवान मिला!
Translated: He got a flattering offer!
Original: क्या वैज्ञानिकों ने नई खोज की है?
Translated: What have scientists discovered newly?
Original: टीम नई सुविधाओं का परीक्षण करती है।
Translated: The team tests new features.


## **QLora fine-tuning**

### Bits optimization

#### bits = 4 (BEST)

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=True
    )

    # Set group size through environment variable
    import os
    os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 346.78 seconds
Epoch 1.9977502812148482 took 352.97 seconds
Epoch 2.996625421822272 took 352.35 seconds
Epoch 4.0 took 350.56 seconds
Epoch 4.99437570303712 took 339.98 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [23:04<00:00,  1.10it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     667.192871                                        30.338867                       348.530216      0.822099    0.763457                0.894837                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# Inference time should be calculated after the model is saved, after fine-tuning the gradients are attached to the layers, which adds up the actual inference time during deployment. Hence, inference time is calculated again in the below code.

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': 0,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': 0,
        'avg_training_time_per_epoch_sec': 0,
        'meteor_score': 0,
        'chrf_score': 0,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': 0,
        'trainable_parameters_after_qlora': 0,
        'lora_parameters': 0,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Quantized mBART model GPU memory usage: 2340.27 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [09:53<00:00,  2.57it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                    0                                        0                       0      0    0                0.378477                                  0                           0          0
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


#### bits = 8

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    bnb_config = BitsAndBytesConfig(
        load_in_8bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=True
    )

    # Set group size through environment variable
    import os
    os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/bitsandbytes/autograd/_functions.py:316: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


Epoch 4.99437570303712 took 592.36 seconds


/usr/local/lib/python3.10/dist-packages/bitsandbytes/autograd/_functions.py:316: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


QLoRA fine-tuned model additional GPU memory usage after training: 37.01 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2
Evaluating the model.


 72%|███████▏  | 1097/1523 [27:21<12:35,  1.77s/it]

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 2337.78 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [10:41<00:00,  2.37it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                    2337.783691                                        37.008789                       592.165087      0.820834    0.760636                0.408405                                  0                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


### Double Quant optimization

#### True

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=True
    )

    # Set group size through environment variable
    import os
    os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 346.78 seconds
Epoch 1.9977502812148482 took 352.97 seconds
Epoch 2.996625421822272 took 352.35 seconds
Epoch 4.0 took 350.56 seconds
Epoch 4.99437570303712 took 339.98 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [23:04<00:00,  1.10it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     667.192871                                        30.338867                       348.530216      0.822099    0.763457                0.894837                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# Inference time should be calculated after the model is saved, after fine-tuning the gradients are attached to the layers, which adds up the actual inference time during deployment. Hence, inference time that was calculated in the experiment- bits=4 was used.

#### False

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 367.19 seconds
Epoch 1.9977502812148482 took 310.60 seconds
Epoch 2.996625421822272 took 311.97 seconds
Epoch 4.0 took 310.32 seconds
Epoch 4.99437570303712 took 309.34 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [18:30<00:00,  1.37it/s]



Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     682.730957                                        30.338867                       321.884743      0.823547    0.763626                0.716779                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# Inference time should be calculated after the model is saved, after fine-tuning the gradients are attached to the layers, which adds up the actual inference time during deployment. Hence, inference time that will be calculated in the experiment- compute_dtype = float16 will be used.

### Compute_dtype Optimization

#### dtype = float16

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.float16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_computedtype_optimization1"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 367.19 seconds
Epoch 1.9977502812148482 took 310.60 seconds
Epoch 2.996625421822272 took 311.97 seconds
Epoch 4.0 took 310.32 seconds
Epoch 4.99437570303712 took 309.34 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [18:30<00:00,  1.37it/s]



Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     682.730957                                        30.338867                       321.884743      0.823547    0.763626                0.716779                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# Inference time should be calculated after the model is saved, after fine-tuning the gradients are attached to the layers, which adds up the actual inference time during deployment. Hence, inference time is calculated again below.

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_computedtype_optimization1",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    global evaluation_results
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': 0,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': 0,
        'avg_training_time_per_epoch_sec': 0,
        'meteor_score': 0,
        'chrf_score': 0,
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': 0,
        'trainable_parameters_after_qlora': 0,
        'lora_parameters': 0,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 2340.27 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [09:27<00:00,  2.68it/s]



Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                              0                                                0                                0             0           0                0.361703                                  0                                 0                0
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


#### dtype = bfloat16

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Quantized mBART model GPU memory usage: 682.73 MB
Trainable parameters before QLoRA: 258287616
Loading data from directory.
Preparing datasets.


/usr/local/lib/python3.10/dist-packages/multiprocess/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 317.89 seconds
Epoch 1.9977502812148482 took 314.43 seconds
Epoch 2.996625421822272 took 315.86 seconds
Epoch 4.0 took 313.62 seconds
Epoch 4.99437570303712 took 333.77 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [19:42<00:00,  1.29it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     682.730957                                        30.338867                       319.113973      0.823402    0.765247                0.763868                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# Inference time should be calculated after the model is saved, after fine-tuning the gradients are attached to the layers, which adds up the actual inference time during deployment. Hence, inference time is calculated again below.

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    global evaluation_results
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': 0,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': 0,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 2340.27 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [10:35<00:00,  2.40it/s]


NameError: name 'avg_epoch_time' is not defined

In [ ]:
evaluation_results

{'meteor': 0.8221666073828205,
 'chrf': 0.7634230009684619,
 'avg_inference_time': 0.40373522923795785}

### Paged Optimization

#### paged optimization = True

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Quantized mBART model GPU memory usage: 682.73 MB
Trainable parameters before QLoRA: 258287616
Loading data from directory.
Preparing datasets.


/usr/local/lib/python3.10/dist-packages/multiprocess/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 317.89 seconds
Epoch 1.9977502812148482 took 314.43 seconds
Epoch 2.996625421822272 took 315.86 seconds
Epoch 4.0 took 313.62 seconds
Epoch 4.99437570303712 took 333.77 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 30.34 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [19:42<00:00,  1.29it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     682.730957                                        30.338867                       319.113973      0.823402    0.765247                0.763868                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    global evaluation_results
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': 0,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': 0,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 2340.27 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [10:35<00:00,  2.40it/s]


NameError: name 'avg_epoch_time' is not defined

In [ ]:
evaluation_results

{'meteor': 0.8221666073828205,
 'chrf': 0.7634230009684619,
 'avg_inference_time': 0.40373522923795785}

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import (
    MBartForConditionalGeneration,
    MBart50Tokenizer,
    Trainer,
    TrainingArguments,
    TrainerCallback,
    BitsAndBytesConfig
)
from datasets import Dataset
from peft import (
    get_peft_model,
    LoraConfig,
    TaskType,
    prepare_model_for_kbit_training
)
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time
import psutil
import matplotlib.pyplot as plt
import seaborn as sns
from dataclasses import dataclass
import json
import numpy as np

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

@dataclass
class MemoryMetrics:
    timestamp: float
    step: int
    gpu_allocated_gb: float
    gpu_peak_gb: float
    gpu_reserved_gb: float
    cpu_percent: float
    cpu_memory_gb: float
    batch_time_ms: float

class DetailedMemoryTracker(TrainerCallback):
    def __init__(self, label: str):
        self.metrics = []
        self.label = label
        self.last_time = time.time()

    def on_step_begin(self, args, state, control, **kwargs):
        self.last_time = time.time()

    def on_step_end(self, args, state, control, **kwargs):
        current_time = time.time()
        batch_time = (current_time - self.last_time) * 1000  # Convert to ms

        metrics = MemoryMetrics(
            timestamp=current_time,
            step=state.global_step,
            gpu_allocated_gb=torch.cuda.memory_allocated() / (1024**3),
            gpu_peak_gb=torch.cuda.max_memory_allocated() / (1024**3),
            gpu_reserved_gb=torch.cuda.memory_reserved() / (1024**3),
            cpu_percent=psutil.Process().cpu_percent(),
            cpu_memory_gb=psutil.Process().memory_info().rss / (1024**3),
            batch_time_ms=batch_time
        )

        self.metrics.append(metrics)
        self.last_time = current_time

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def create_visualizations(metrics_data, save_dir='results'):
    """Create and save comprehensive visualizations"""
    os.makedirs(save_dir, exist_ok=True)
    plt.style.use('seaborn-v0_8-paper')

    # Convert metrics to DataFrame
    df = pd.DataFrame([vars(m) for m in metrics_data['metrics']])

    # 1. Memory Usage Over Time
    plt.figure(figsize=(12, 6))
    plt.plot(df['step'], df['gpu_peak_gb'], label='Peak Memory', color='blue')
    plt.plot(df['step'], df['gpu_allocated_gb'], label='Allocated Memory', color='green')
    plt.plot(df['step'], df['gpu_reserved_gb'], label='Reserved Memory', color='red')
    plt.xlabel('Training Steps')
    plt.ylabel('GPU Memory Usage (GB)')
    plt.title('GPU Memory Usage During Training')
    plt.legend()
    plt.grid(True)
    plt.savefig(f'{save_dir}/memory_usage_over_time.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 2. Memory Distribution
    plt.figure(figsize=(10, 6))
    memory_data = df[['gpu_allocated_gb', 'gpu_peak_gb', 'gpu_reserved_gb']]
    memory_data.columns = ['Allocated', 'Peak', 'Reserved']  # Rename for better labels
    sns.violinplot(data=pd.melt(memory_data), x='variable', y='value')
    plt.ylabel('GPU Memory Usage (GB)')
    plt.title('Distribution of GPU Memory Usage')
    plt.xticks(rotation=45)
    plt.savefig(f'{save_dir}/memory_distribution.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 3. Training Time Analysis
    plt.figure(figsize=(10, 6))
    sns.histplot(data=df['batch_time_ms'], bins=50)
    plt.xlabel('Batch Time (ms)')
    plt.ylabel('Frequency')
    plt.title('Distribution of Batch Processing Times')
    plt.savefig(f'{save_dir}/batch_time_distribution.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 4. CPU Usage and Memory
    fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(12, 8))

    ax1.plot(df['step'], df['cpu_percent'], color='purple')
    ax1.set_xlabel('Training Steps')
    ax1.set_ylabel('CPU Usage (%)')
    ax1.set_title('CPU Usage Over Time')
    ax1.grid(True)

    ax2.plot(df['step'], df['cpu_memory_gb'], color='orange')
    ax2.set_xlabel('Training Steps')
    ax2.set_ylabel('CPU Memory (GB)')
    ax2.set_title('CPU Memory Usage Over Time')
    ax2.grid(True)

    plt.tight_layout()
    plt.savefig(f'{save_dir}/cpu_metrics.png', dpi=300, bbox_inches='tight')
    plt.close()

    # Save metrics summary
    summary = {
        'peak_gpu_memory_gb': df['gpu_peak_gb'].max(),
        'avg_gpu_memory_gb': df['gpu_allocated_gb'].mean(),
        'peak_cpu_memory_gb': df['cpu_memory_gb'].max(),
        'avg_cpu_memory_gb': df['cpu_memory_gb'].mean(),
        'avg_batch_time_ms': df['batch_time_ms'].mean(),
        'total_training_time_min': (df['timestamp'].max() - df['timestamp'].min()) / 60,
        'additional_metrics': metrics_data.get('enhanced_metrics', {})
    }

    with open(f'{save_dir}/training_summary.json', 'w') as f:
        json.dump(summary, f, indent=2)

    return summary

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

def fine_tune_model(model, train_dataset, val_dataset, trainable_params_before):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    # Replace TimerCallback with DetailedMemoryTracker
    memory_tracker = DetailedMemoryTracker(label="QLoRA")

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[memory_tracker],
    )

    # Track training start time
    start_time = time.time()
    trainer.train()
    total_training_time = time.time() - start_time

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    # Collect enhanced metrics
    enhanced_metrics = {
        'quantized_model_gpu_memory_mb': before_qlora,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': gpu_increase,
        'avg_training_time_per_epoch_sec': total_training_time / training_args.num_train_epochs,
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params
    }

    # Create results dictionary
    training_results = {
        'metrics': memory_tracker.metrics,
        'training_time': total_training_time,
        'enhanced_metrics': enhanced_metrics
    }

    # Generate visualizations
    summary = create_visualizations(training_results)

    # Save the model
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to: {drive_save_path}")

    return model, training_results, summary

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, training_results, training_summary = fine_tune_model(
        model, train_dataset, val_dataset, trainable_params_before
    )

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    # Combine all metrics
    final_metrics = {
        **training_summary,
        'evaluation_metrics': {
            'meteor_score': evaluation_results['meteor'],
            'chrf_score': evaluation_results['chrf'],
            'avg_inference_time_sec': evaluation_results['avg_inference_time']
        }
    }

    # Create and save final results
    results_df = pd.DataFrame([final_metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Create results directory structure
    drive_results_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/results"
    os.makedirs(drive_results_dir, exist_ok=True)

    # Save detailed results
    results_path = f"{drive_results_dir}/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(results_path)

    # Save raw metrics
    metrics_path = f"{drive_results_dir}/detailed_metrics.json"
    with open(metrics_path, 'w') as f:
      json.dump({
                'training_metrics': training_results,
                'evaluation_metrics': evaluation_results,
                'summary': training_summary
            }, f, indent=2)

      # Save training plots
      plots_dir = f"{drive_results_dir}/plots"
      os.makedirs(plots_dir, exist_ok=True)

      # Create additional visualization: Training Progress
      metrics_df = pd.DataFrame([vars(m) for m in training_results['metrics']])

      plt.figure(figsize=(15, 10))

      # Plot 1: Memory Usage
      plt.subplot(2, 2, 1)
      plt.plot(metrics_df['step'], metrics_df['allocated_gb'], label='Allocated')
      plt.plot(metrics_df['step'], metrics_df['peak_gb'], label='Peak')
      plt.title('GPU Memory Usage Over Time')
      plt.xlabel('Training Steps')
      plt.ylabel('Memory (GB)')
      plt.legend()

      # Plot 2: CPU Usage
      plt.subplot(2, 2, 2)
      plt.plot(metrics_df['step'], metrics_df['cpu_percent'])
      plt.title('CPU Usage Over Time')
      plt.xlabel('Training Steps')
      plt.ylabel('CPU Usage (%)')

      # Plot 3: Batch Time Distribution
      plt.subplot(2, 2, 3)
      sns.histplot(data=metrics_df['batch_time_ms'], bins=50)
      plt.title('Batch Processing Time Distribution')
      plt.xlabel('Time (ms)')
      plt.ylabel('Frequency')

      # Plot 4: Memory Distribution
      plt.subplot(2, 2, 4)
      sns.boxplot(data=metrics_df[['allocated_gb', 'peak_gb', 'reserved_gb']])
      plt.title('Memory Usage Distribution')
      plt.ylabel('Memory (GB)')
      plt.xticks(rotation=45)

      plt.tight_layout()
      plt.savefig(f"{plots_dir}/training_progress_summary.png", dpi=300, bbox_inches='tight')
      plt.close()

      # Create performance metrics summary
      performance_summary = {
            'Training': {
                'Total Time (minutes)': training_results['training_time'] / 60,
                'Average Batch Time (ms)': metrics_df['batch_time_ms'].mean(),
                'Peak GPU Memory (GB)': metrics_df['peak_gb'].max(),
                'Average GPU Memory (GB)': metrics_df['allocated_gb'].mean(),
                'Peak CPU Usage (%)': metrics_df['cpu_percent'].max()
            },
            'Model': {
                'Parameters Before QLoRA': trainable_params_before,
                'Parameters After QLoRA': training_results['enhanced_metrics']['trainable_parameters_after_qlora'],
                'LoRA Parameters': training_results['enhanced_metrics']['lora_parameters']
            },
            'Evaluation': {
                'METEOR Score': evaluation_results['meteor'],
                'CHRF Score': evaluation_results['chrf'],
                'Average Inference Time (s)': evaluation_results['avg_inference_time']
            }
        }

      # Save performance summary
      with open(f"{drive_results_dir}/performance_summary.json", 'w') as f:
        json.dump(performance_summary, f, indent=2)

        # Create a markdown report
      report_content = f"""
# QLoRA Fine-tuning Report for mBART
Generated on: {time.strftime('%Y-%m-%d %H:%M:%S')}

## Training Performance
- Total Training Time: {performance_summary['Training']['Total Time (minutes)']:.2f} minutes
- Average Batch Processing Time: {performance_summary['Training']['Average Batch Time (ms)']:.2f} ms
- Peak GPU Memory Usage: {performance_summary['Training']['Peak GPU Memory (GB)']:.2f} GB
- Average GPU Memory Usage: {performance_summary['Training']['Average GPU Memory (GB)']:.2f} GB
- Peak CPU Usage: {performance_summary['Training']['Peak CPU Usage (%)']:.2f}%

## Model Statistics
- Initial Trainable Parameters: {performance_summary['Model']['Parameters Before QLoRA']:,}
- Final Trainable Parameters: {performance_summary['Model']['Parameters After QLoRA']:,}
- LoRA Parameters: {performance_summary['Model']['LoRA Parameters']:,}

## Evaluation Metrics
- METEOR Score: {performance_summary['Evaluation']['METEOR Score']:.4f}
- CHRF Score: {performance_summary['Evaluation']['CHRF Score']:.4f}
- Average Inference Time: {performance_summary['Evaluation']['Average Inference Time (s)']:.4f} seconds

## Files Generated
- Model weights: /qlora_fine_tuned_mbart
- Performance metrics: /results/qlora_fine_tuned_mbart_performance.csv
- Detailed metrics: /results/detailed_metrics.json
- Training visualizations: /results/plots/
        """

      # Save the report
      with open(f"{drive_results_dir}/training_report.md", 'w') as f:
        f.write(report_content)

      print(f"\nTraining complete! All results have been saved to: {drive_results_dir}")
      print("\nGenerated files:")
      print(f"- Model weights: {drive_save_path}")
      print(f"- Performance metrics: {results_path}")
      print(f"- Detailed metrics: {metrics_path}")
      print(f"- Training visualizations: {plots_dir}")
      print(f"- Training report: {drive_results_dir}/training_report.md")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 682.73 MB
Trainable parameters before QLoRA: 258287616
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

Map (num_proc=2):   0%|          | 0/1523 [00:00<?, ? examples/s]

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Model saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [19:51<00:00,  1.28it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         peak_gpu_memory_gb  avg_gpu_memory_gb  peak_cpu_memory_gb  avg_cpu_memory_gb  avg_batch_time_ms  total_training_time_min                                                                                                                                                                                                                                                                                  additional_metrics                                                                                                    evaluation_metrics
Overall            5.696092            1.37687             2.30146           2.301459          990.44479                28.096015  {'quantized_model_gpu_memory_mb': 1395.80078125, 'qlora_fine_tuned_model_additional_gpu_memory_mb': 14.0888671875, 'avg_training_time_per_epoch_sec': 343.69564471244814, 'trainable_parameters_before_qlora': 258287616, 'trainable_parameters_after_qlora': 2359296, 'lora_parameters':

TypeError: Object of type MemoryMetrics is not JSON serializable

#### paged optimization = False

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}

    # Define file mappings
    file_mappings = {
        'train': 'train_split.csv',
        'validation': 'validation_split.csv',
        'test': 'test_split.csv'
    }

    # Process each split
    for split, filename in file_mappings.items():
        file_path = os.path.join(base_path, filename)
        df = pd.read_csv(file_path)
        hindi_sentences = df['Hindi_Text'].tolist()
        english_sentences = df['English_Text'].tolist()
        data[split].extend(zip(hindi_sentences, english_sentences))

    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    from transformers import BitsAndBytesConfig

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="adamw_torch",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': original_model_memory,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': qlora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

...

Fine-tuning the model with QLoRA.
trainable params: 2,359,296 || all params: 613,238,784 || trainable%: 0.3847


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Epoch 0.9988751406074241 took 319.25 seconds
Epoch 1.9977502812148482 took 317.24 seconds
Epoch 2.996625421822272 took 317.77 seconds
Epoch 4.0 took 317.32 seconds
Epoch 4.99437570303712 took 315.65 seconds
QLoRA fine-tuned model additional GPU memory usage after training: 43.70 MB
Trainable parameters after training: 2359296
LoRA parameters after training: 2359296
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [19:14<00:00,  1.32it/s]



Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                     682.730957                                        43.696289                       317.443901      0.821825    0.761454                0.744829                          258287616                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
# peak gpu memory= 8.2 GB

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import MBartForConditionalGeneration, MBart50Tokenizer, Trainer, TrainingArguments, TrainerCallback, BitsAndBytesConfig
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType, prepare_model_for_kbit_training
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    # bnb_config = BitsAndBytesConfig(
    #     load_in_8bit=True,
    #     bnb_4bit_quant_type="nf4",
    #     bnb_4bit_compute_dtype=torch.float16,
    #     bnb_4bit_use_double_quant=True
    # )

    # # Set group size through environment variable
    # import os
    # os.environ["BNB_4BIT_GROUP_SIZE"] = "128"

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart",
        device_map={'': 'cuda'}
        # quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    # Updated LoRA configuration
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="paged_adamw_8bit",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora
    print(f"QLoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    print(f"Trainable parameters after training: {trainable_params_after}")
    print(f"LoRA parameters after training: {lora_params}")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_bit_optimization2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, trainable_params_after, lora_params, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}  # Move inputs to the same device as the model

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    global evaluation_results
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    # print("Preparing datasets.")
    # train_dataset = prepare_dataset(data['train'], tokenizer)
    # val_dataset = prepare_dataset(data['validation'], tokenizer)

    # print("Fine-tuning the model with QLoRA.")
    # fine_tuned_model, qlora_memory_increase, trainable_params_after, lora_params, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(model, tokenizer, test_data)

    metrics = {
        'quantized_model_gpu_memory_mb': 0,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': 0,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf'],
        'avg_inference_time_sec': evaluation_results['avg_inference_time'],
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params,
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model
Quantized mBART model GPU memory usage: 2340.27 MB
Trainable parameters before QLoRA: 0
Loading data from directory.
Evaluating the model.


100%|██████████| 1523/1523 [09:45<00:00,  2.60it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         quantized_model_gpu_memory_mb  qlora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score  avg_inference_time_sec  trainable_parameters_before_qlora  trainable_parameters_after_qlora  lora_parameters
Overall                              0                                                0                       317.443901      0.824568    0.762544                0.372577                                  0                           2359296          2359296
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart_performance.csv


In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader
from transformers import (
    MBartForConditionalGeneration,
    MBart50Tokenizer,
    Trainer,
    TrainingArguments,
    TrainerCallback,
    BitsAndBytesConfig
)
from datasets import Dataset
from peft import (
    get_peft_model,
    LoraConfig,
    TaskType,
    prepare_model_for_kbit_training
)
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time
import psutil
import matplotlib.pyplot as plt
import seaborn as sns
from dataclasses import dataclass
import json
import numpy as np

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

@dataclass
class MemoryMetrics:
    timestamp: float
    step: int
    gpu_allocated_gb: float
    gpu_peak_gb: float
    gpu_reserved_gb: float
    cpu_percent: float
    cpu_memory_gb: float
    batch_time_ms: float

class DetailedMemoryTracker(TrainerCallback):
    def __init__(self, label: str):
        self.metrics = []
        self.label = label
        self.last_time = time.time()

    def on_step_begin(self, args, state, control, **kwargs):
        self.last_time = time.time()

    def on_step_end(self, args, state, control, **kwargs):
        current_time = time.time()
        batch_time = (current_time - self.last_time) * 1000  # Convert to ms

        metrics = MemoryMetrics(
            timestamp=current_time,
            step=state.global_step,
            gpu_allocated_gb=torch.cuda.memory_allocated() / (1024**3),
            gpu_peak_gb=torch.cuda.max_memory_allocated() / (1024**3),
            gpu_reserved_gb=torch.cuda.memory_reserved() / (1024**3),
            cpu_percent=psutil.Process().cpu_percent(),
            cpu_memory_gb=psutil.Process().memory_info().rss / (1024**3),
            batch_time_ms=batch_time
        )

        self.metrics.append(metrics)
        self.last_time = current_time

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_data_from_directory(base_path):
    data = {'train': [], 'validation': [], 'test': []}
    for split in ['train_set', 'validation_set', 'test_set']:
        split_path = os.path.join(base_path, split)
        for root, dirs, files in os.walk(split_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    df = pd.read_csv(file_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    if split == 'train_set':
                        data['train'].extend(zip(hindi_sentences, english_sentences))
                    elif split == 'validation_set':
                        data['validation'].extend(zip(hindi_sentences, english_sentences))
                    else:
                        data['test'].extend(zip(hindi_sentences, english_sentences))
    return data

def count_trainable_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

def count_lora_parameters(model):
    return sum(p.numel() for n, p in model.named_parameters() if "lora_" in n)

def create_visualizations(metrics_data, save_dir='results'):
    """Create and save comprehensive visualizations"""
    os.makedirs(save_dir, exist_ok=True)
    plt.style.use('seaborn-v0_8-paper')

    # Convert metrics to DataFrame
    df = pd.DataFrame([vars(m) for m in metrics_data['metrics']])

    # 1. Memory Usage Over Time
    plt.figure(figsize=(12, 6))
    plt.plot(df['step'], df['gpu_peak_gb'], label='Peak Memory', color='blue')
    plt.plot(df['step'], df['gpu_allocated_gb'], label='Allocated Memory', color='green')
    plt.plot(df['step'], df['gpu_reserved_gb'], label='Reserved Memory', color='red')
    plt.xlabel('Training Steps')
    plt.ylabel('GPU Memory Usage (GB)')
    plt.title('GPU Memory Usage During Training')
    plt.legend()
    plt.grid(True)
    plt.savefig(f'{save_dir}/memory_usage_over_time.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 2. Memory Distribution
    plt.figure(figsize=(10, 6))
    memory_data = df[['gpu_allocated_gb', 'gpu_peak_gb', 'gpu_reserved_gb']]
    memory_data.columns = ['Allocated', 'Peak', 'Reserved']  # Rename for better labels
    sns.violinplot(data=pd.melt(memory_data), x='variable', y='value')
    plt.ylabel('GPU Memory Usage (GB)')
    plt.title('Distribution of GPU Memory Usage')
    plt.xticks(rotation=45)
    plt.savefig(f'{save_dir}/memory_distribution.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 3. Training Time Analysis
    plt.figure(figsize=(10, 6))
    sns.histplot(data=df['batch_time_ms'], bins=50)
    plt.xlabel('Batch Time (ms)')
    plt.ylabel('Frequency')
    plt.title('Distribution of Batch Processing Times')
    plt.savefig(f'{save_dir}/batch_time_distribution.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 4. CPU Usage and Memory
    fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(12, 8))

    ax1.plot(df['step'], df['cpu_percent'], color='purple')
    ax1.set_xlabel('Training Steps')
    ax1.set_ylabel('CPU Usage (%)')
    ax1.set_title('CPU Usage Over Time')
    ax1.grid(True)

    ax2.plot(df['step'], df['cpu_memory_gb'], color='orange')
    ax2.set_xlabel('Training Steps')
    ax2.set_ylabel('CPU Memory (GB)')
    ax2.set_title('CPU Memory Usage Over Time')
    ax2.grid(True)

    plt.tight_layout()
    plt.savefig(f'{save_dir}/cpu_metrics.png', dpi=300, bbox_inches='tight')
    plt.close()

    # Save metrics summary
    summary = {
        'peak_gpu_memory_gb': df['gpu_peak_gb'].max(),
        'avg_gpu_memory_gb': df['gpu_allocated_gb'].mean(),
        'peak_cpu_memory_gb': df['cpu_memory_gb'].max(),
        'avg_cpu_memory_gb': df['cpu_memory_gb'].mean(),
        'avg_batch_time_ms': df['batch_time_ms'].mean(),
        'total_training_time_min': (df['timestamp'].max() - df['timestamp'].min()) / 60,
        'additional_metrics': metrics_data.get('enhanced_metrics', {})
    }

    with open(f'{save_dir}/training_summary.json', 'w') as f:
        json.dump(summary, f, indent=2)

    return summary

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    # Load tokenizer
    tokenizer = MBart50Tokenizer.from_pretrained(
        model_checkpoint,
        clean_up_tokenization_spaces=True
    )

    bnb_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=False
    )

    # Load model
    model = MBartForConditionalGeneration.from_pretrained(
        model_checkpoint,
        device_map={'': 'cuda'},
        quantization_config=bnb_config
    )

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Quantized mBART model GPU memory usage: {gpu_increase:.2f} MB")

    trainable_params_before = count_trainable_parameters(model)
    print(f"Trainable parameters before QLoRA: {trainable_params_before}")

    return model, tokenizer, gpu_increase, trainable_params_before

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

def fine_tune_model(model, train_dataset, val_dataset, trainable_params_before):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        target_modules=["k_proj", "v_proj"],
        lora_dropout=0.0,
    )

    before_qlora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()

    # Replace TimerCallback with DetailedMemoryTracker
    memory_tracker = DetailedMemoryTracker(label="QLoRA")

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        learning_rate=1e-4,
        fp16=True,
        gradient_accumulation_steps=4,
        optim="adamw_torch",
        report_to="none"
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[memory_tracker],
    )

    # Track training start time
    start_time = time.time()
    trainer.train()
    total_training_time = time.time() - start_time

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_qlora

    trainable_params_after = count_trainable_parameters(model)
    lora_params = count_lora_parameters(model)

    # Collect enhanced metrics
    enhanced_metrics = {
        'quantized_model_gpu_memory_mb': before_qlora,
        'qlora_fine_tuned_model_additional_gpu_memory_mb': gpu_increase,
        'avg_training_time_per_epoch_sec': total_training_time / training_args.num_train_epochs,
        'trainable_parameters_before_qlora': trainable_params_before,
        'trainable_parameters_after_qlora': trainable_params_after,
        'lora_parameters': lora_params
    }

    # Create results dictionary
    training_results = {
        'metrics': memory_tracker.metrics,
        'training_time': total_training_time,
        'enhanced_metrics': enhanced_metrics
    }

    # Generate visualizations
    summary = create_visualizations(training_results)

    # Save the model
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to: {drive_save_path}")

    return model, training_results, summary

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length)
    inputs = {k: v.to(model.device) for k, v in inputs.items()}

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model(model, tokenizer, test_data):
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}
    inference_times = []
    for hindi, english in tqdm(test_data):
        translation, inf_time = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)
        inference_times.append(inf_time)

    avg_inference_time = sum(inference_times) / len(inference_times)
    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    metrics['avg_inference_time'] = avg_inference_time
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory, trainable_params_before = load_model()

    print("Loading data from directory.")
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted"
    data = load_data_from_directory(base_path)

    print("Preparing datasets.")
    train_dataset = prepare_dataset(data['train'], tokenizer)
    val_dataset = prepare_dataset(data['validation'], tokenizer)

    print("Fine-tuning the model with QLoRA.")
    fine_tuned_model, training_results, training_summary = fine_tune_model(
        model, train_dataset, val_dataset, trainable_params_before
    )

    print("Evaluating the model.")
    test_data = data['test']
    evaluation_results = evaluate_model(fine_tuned_model, tokenizer, test_data)

    # Combine all metrics
    final_metrics = {
        **training_summary,
        'evaluation_metrics': {
            'meteor_score': evaluation_results['meteor'],
            'chrf_score': evaluation_results['chrf'],
            'avg_inference_time_sec': evaluation_results['avg_inference_time']
        }
    }

    # Create and save final results
    results_df = pd.DataFrame([final_metrics])
    results_df.index = ['Overall']

    print("\nSummary of Results for QLoRA Fine-tuned mBART:")
    print(results_df.to_string())

    # Create results directory structure
    drive_results_dir = "/content/drive/MyDrive/Colab Notebooks/Translation Models/results"
    os.makedirs(drive_results_dir, exist_ok=True)

    # Save detailed results
    results_path = f"{drive_results_dir}/qlora_fine_tuned_mbart_performance.csv"
    results_df.to_csv(results_path)

    # Save raw metrics
    metrics_path = f"{drive_results_dir}/detailed_metrics.json"
    with open(metrics_path, 'w') as f:
      json.dump({
                'training_metrics': training_results,
                'evaluation_metrics': evaluation_results,
                'summary': training_summary
            }, f, indent=2)

      # Save training plots
      plots_dir = f"{drive_results_dir}/plots"
      os.makedirs(plots_dir, exist_ok=True)

      # Create additional visualization: Training Progress
      metrics_df = pd.DataFrame([vars(m) for m in training_results['metrics']])

      plt.figure(figsize=(15, 10))

      # Plot 1: Memory Usage
      plt.subplot(2, 2, 1)
      plt.plot(metrics_df['step'], metrics_df['allocated_gb'], label='Allocated')
      plt.plot(metrics_df['step'], metrics_df['peak_gb'], label='Peak')
      plt.title('GPU Memory Usage Over Time')
      plt.xlabel('Training Steps')
      plt.ylabel('Memory (GB)')
      plt.legend()

      # Plot 2: CPU Usage
      plt.subplot(2, 2, 2)
      plt.plot(metrics_df['step'], metrics_df['cpu_percent'])
      plt.title('CPU Usage Over Time')
      plt.xlabel('Training Steps')
      plt.ylabel('CPU Usage (%)')

      # Plot 3: Batch Time Distribution
      plt.subplot(2, 2, 3)
      sns.histplot(data=metrics_df['batch_time_ms'], bins=50)
      plt.title('Batch Processing Time Distribution')
      plt.xlabel('Time (ms)')
      plt.ylabel('Frequency')

      # Plot 4: Memory Distribution
      plt.subplot(2, 2, 4)
      sns.boxplot(data=metrics_df[['allocated_gb', 'peak_gb', 'reserved_gb']])
      plt.title('Memory Usage Distribution')
      plt.ylabel('Memory (GB)')
      plt.xticks(rotation=45)

      plt.tight_layout()
      plt.savefig(f"{plots_dir}/training_progress_summary.png", dpi=300, bbox_inches='tight')
      plt.close()

      # Create performance metrics summary
      performance_summary = {
            'Training': {
                'Total Time (minutes)': training_results['training_time'] / 60,
                'Average Batch Time (ms)': metrics_df['batch_time_ms'].mean(),
                'Peak GPU Memory (GB)': metrics_df['peak_gb'].max(),
                'Average GPU Memory (GB)': metrics_df['allocated_gb'].mean(),
                'Peak CPU Usage (%)': metrics_df['cpu_percent'].max()
            },
            'Model': {
                'Parameters Before QLoRA': trainable_params_before,
                'Parameters After QLoRA': training_results['enhanced_metrics']['trainable_parameters_after_qlora'],
                'LoRA Parameters': training_results['enhanced_metrics']['lora_parameters']
            },
            'Evaluation': {
                'METEOR Score': evaluation_results['meteor'],
                'CHRF Score': evaluation_results['chrf'],
                'Average Inference Time (s)': evaluation_results['avg_inference_time']
            }
        }

      # Save performance summary
      with open(f"{drive_results_dir}/performance_summary.json", 'w') as f:
        json.dump(performance_summary, f, indent=2)

        # Create a markdown report
      report_content = f"""
# QLoRA Fine-tuning Report for mBART
Generated on: {time.strftime('%Y-%m-%d %H:%M:%S')}

## Training Performance
- Total Training Time: {performance_summary['Training']['Total Time (minutes)']:.2f} minutes
- Average Batch Processing Time: {performance_summary['Training']['Average Batch Time (ms)']:.2f} ms
- Peak GPU Memory Usage: {performance_summary['Training']['Peak GPU Memory (GB)']:.2f} GB
- Average GPU Memory Usage: {performance_summary['Training']['Average GPU Memory (GB)']:.2f} GB
- Peak CPU Usage: {performance_summary['Training']['Peak CPU Usage (%)']:.2f}%

## Model Statistics
- Initial Trainable Parameters: {performance_summary['Model']['Parameters Before QLoRA']:,}
- Final Trainable Parameters: {performance_summary['Model']['Parameters After QLoRA']:,}
- LoRA Parameters: {performance_summary['Model']['LoRA Parameters']:,}

## Evaluation Metrics
- METEOR Score: {performance_summary['Evaluation']['METEOR Score']:.4f}
- CHRF Score: {performance_summary['Evaluation']['CHRF Score']:.4f}
- Average Inference Time: {performance_summary['Evaluation']['Average Inference Time (s)']:.4f} seconds

## Files Generated
- Model weights: /qlora_fine_tuned_mbart
- Performance metrics: /results/qlora_fine_tuned_mbart_performance.csv
- Detailed metrics: /results/detailed_metrics.json
- Training visualizations: /results/plots/
        """

      # Save the report
      with open(f"{drive_results_dir}/training_report.md", 'w') as f:
        f.write(report_content)

      print(f"\nTraining complete! All results have been saved to: {drive_results_dir}")
      print("\nGenerated files:")
      print(f"- Model weights: {drive_save_path}")
      print(f"- Performance metrics: {results_path}")
      print(f"- Detailed metrics: {metrics_path}")
      print(f"- Training visualizations: {plots_dir}")
      print(f"- Training report: {drive_results_dir}/training_report.md")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Quantized mBART model GPU memory usage: 682.73 MB
Trainable parameters before QLoRA: 258287616
Loading data from directory.
Preparing datasets.


Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Model saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart
Evaluating the model.


100%|██████████| 1523/1523 [19:48<00:00,  1.28it/s]


Summary of Results for QLoRA Fine-tuned mBART:
         peak_gpu_memory_gb  avg_gpu_memory_gb  peak_cpu_memory_gb  avg_cpu_memory_gb  avg_batch_time_ms  total_training_time_min                                                                                                                                                                                                                                                                                   additional_metrics                                                                                                    evaluation_metrics
Overall            5.986444           0.709426            1.976059           1.975151        1048.087308                29.107619  {'quantized_model_gpu_memory_mb': 682.73095703125, 'qlora_fine_tuned_model_additional_gpu_memory_mb': 43.6962890625, 'avg_training_time_per_epoch_sec': 357.1186255455017, 'trainable_parameters_before_qlora': 258287616, 'trainable_parameters_after_qlora': 2359296, 'lora_parameters

TypeError: Object of type MemoryMetrics is not JSON serializable

## **Translation Examples**

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
import os
from tabulate import tabulate

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

test_data = [
    {
        "hindi": "उन्होंने अपने व्यापार को बढ़ाने के लिए बहुत पापड़ बेले।",
        "reference": "They went through a lot of trouble to expand their business."
    },
    {
        "hindi": "उसने ईंट का जवाब पत्थर से देकर दुश्मन को करारा सबक सिखाया।",
        "reference": "He gave a befitting reply to the enemy and taught them a harsh lesson."
    },
    {
        "hindi": "आप तो ईद का चाँद हो गए!",
        "reference": "You have become a rare sight!"
    },
    {
        "hindi": "उसने कभी ऊंट के मुँह में जीरा नहीं डाला है।",
        "reference": "She has never offered a drop in the ocean."
    },


    {
        "hindi": "हम भोजन कर रहे होंगे!",
        "reference": "We will be having dinner!"
    },
    {
        "hindi": "क्या वैज्ञानिकों ने नई खोज की है?",
        "reference": "Have the scientists made a new discovery?"
    },
    {
        "hindi": "टीम नई सुविधाओं का परीक्षण करती है।",
        "reference": "The team tests the new features."
    },
    {
        "hindi": "क्या अद्भुत सवारी होगी!",
        "reference": "What a wonderful ride it will be!"
    },
    {
        "hindi": "मुद्दों पर बहस की जा रही होगी।",
        "reference": "Debates on issues will be being conducted."
    },


    {
        "hindi": "वह उल्टा चोर कोतवाल को डाँट रहा था!",
        "reference": "He was blaming others for his own faults!"
    },
    {
        "hindi": "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
        "reference": "He will have accomplished the task without any harm."
    }
]

model_paths = {
    "Base mBART": "facebook/mbart-large-50-many-to-many-mmt",
    "Full Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart",
    "LoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3",
    "QLoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
}

def load_model(model_path):
    """Load model from path, using the base tokenizer"""
    print(f"Loading model from {model_path}...")

    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    model = MBartForConditionalGeneration.from_pretrained(model_path)
    model.to(device)

    return model, tokenizer

def translate_text(text, model, tokenizer, max_length=100):
    """Translate a single Hindi text to English"""
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"

    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    with torch.no_grad():
        translated = model.generate(
            **inputs,
            max_length=max_length,
            forced_bos_token_id=tokenizer.lang_code_to_id["en_XX"]
        )

    output = tokenizer.decode(translated[0], skip_special_tokens=True)
    return output

def main():
    results = []

    models_and_tokenizers = {}
    for model_name, model_path in model_paths.items():
        try:
            model, tokenizer = load_model(model_path)
            models_and_tokenizers[model_name] = (model, tokenizer)
        except Exception as e:
            print(f"Failed to load {model_name}: {str(e)}")
            models_and_tokenizers[model_name] = (None, None)

    for i, data in enumerate(test_data):
        print(f"\nProcessing example {i+1}/{len(test_data)}")
        hindi_text = data["hindi"]
        reference = data["reference"]

        row = {
            "Hindi": hindi_text,
            "Reference": reference
        }

        for model_name, (model, tokenizer) in models_and_tokenizers.items():
            print(f"Translating with {model_name}...")
            if model is None or tokenizer is None:
                row[model_name] = "ERROR: Model not loaded"
                continue

            try:
                translation = translate_text(hindi_text, model, tokenizer)
                row[model_name] = translation
            except Exception as e:
                print(f"Error with {model_name}: {str(e)}")
                row[model_name] = f"ERROR: {str(e)}"

        results.append(row)

    print("\n\n=== TRANSLATION COMPARISON ===\n")
    for i, result in enumerate(results):
        print(f"Example {i+1}:")
        print(f"Hindi: {result['Hindi']}")
        print(f"Reference: {result['Reference']}")
        model_translations = [[model_name, result.get(model_name, "N/A")] for model_name in model_paths.keys()]
        print(tabulate(model_translations, headers=["Model", "Translation"], tablefmt="grid"))
        print("\n" + "-"*80 + "\n")

    print("Translation comparison completed!")

if __name__ == "__main__":
    main()

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Using device: cpu
Loading model from facebook/mbart-large-50-many-to-many-mmt...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart...

Processing example 1/11
Translating with Base mBART...
Translating with Full Fine-tuned...
Translating with LoRA Fine-tuned...
Translating with QLoRA Fine-tuned...

Processing example 2/11
Translating with Base mBART...
Translating with Full Fine-tuned...
Translating with LoRA Fine-tuned...
Translating with QLoRA Fine-tuned...

Processing example 3/11
Translating with Base mBART...
Translating with Full Fine-tuned...
Translating with LoRA Fine-tuned...
Translating with QLoRA Fine-tuned...

Processing example 4/11
Translating with Base mBART...
Translating with Full Fine-tuned...
Translating with LoRA Fine-tuned...
Translating with QLoRA Fine-tuned...

Processing example 5/11
Translating with Base mBART...
Translating with Full Fine-tuned...
Translating with LoRA Fine-tuned...
Translating with QLoRA Fine-tuned...

Processing example 6/11
Translating with Base mBART...
Translating with

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
import os
from tabulate import tabulate

# Check for GPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Hindi test sentences with English reference translations
test_data = [
    {
        "hindi": "क्या अद्भुत सवारी होगी!",
        "reference": "What a wonderful ride it will be!"
    },
    {
        "hindi": "जिम जाओ।",
        "reference": "Go to the gym."
    },
    {
        "hindi": "वह उम्र भर का साथ निभा रहा था।",
        "reference": "He was keeping a lifelong companionship"
    },
    {
        "hindi": "उसने काम ऐसा किया कि साँप भी मर जाए और लाठी भी न टूटे।",
        "reference": "He will have accomplished the task without any harm."
    },
    {
        "hindi": "वह कह रहा है कि राष्ट्रपति चुनाव में कड़ा मुकाबला हो रहा है।",
        "reference": "He is saying that the presidential election is tightly contested."
    },
    {
        "hindi": "मुद्दों पर बहस की जा रही होगी।",
        "reference": "Debates on issues will be being conducted."
    }
]

# Model paths
model_paths = {
    "Base mBART": "facebook/mbart-large-50-many-to-many-mmt",
    "LoRA Alpha 8": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization1",
    "LoRA Alpha 32": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization2",
    "LoRA Alpha 64": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization3",
    "LoRA Alpha 128": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization4",
    "LoRA Alpha 512": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5"
}

def load_model(model_path):
    """Load model from path, using the base tokenizer"""
    print(f"Loading model from {model_path}...")

    # Always load tokenizer from base model
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    # Load model from specified path
    model = MBartForConditionalGeneration.from_pretrained(model_path)
    model.to(device)

    return model, tokenizer

def translate_text(text, model, tokenizer, max_length=100):
    """Translate a single Hindi text to English"""
    tokenizer.src_lang = "hi_IN"  # Hindi
    tokenizer.tgt_lang = "en_XX"  # English

    # Encode Hindi text
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    # Generate translation
    with torch.no_grad():
        translated = model.generate(
            **inputs,
            max_length=max_length,
            forced_bos_token_id=tokenizer.lang_code_to_id["en_XX"]
        )

    # Decode to English
    output = tokenizer.decode(translated[0], skip_special_tokens=True)
    return output

def main():
    results = []

    # Process each test example
    for i, data in enumerate(test_data):
        print(f"\nProcessing example {i+1}/{len(test_data)}")
        hindi_text = data["hindi"]
        reference = data["reference"]

        row = {
            "Hindi": hindi_text,
            "Reference": reference
        }

        # Translate with each model
        for model_name, model_path in model_paths.items():
            print(f"Translating with {model_name}...")
            try:
                # Load model and tokenizer
                model, tokenizer = load_model(model_path)

                # Translate
                translation = translate_text(hindi_text, model, tokenizer)

                # Add to results
                row[model_name] = translation

                # Clear GPU memory
                del model
                torch.cuda.empty_cache() if torch.cuda.is_available() else None

            except Exception as e:
                print(f"Error with {model_name}: {str(e)}")
                row[model_name] = f"ERROR: {str(e)}"

        results.append(row)

    # Display results in a nice table format
    print("\n\n=== TRANSLATION COMPARISON ===\n")

    for i, result in enumerate(results):
        print(f"Example {i+1}:")
        print(f"Hindi: {result['Hindi']}")
        print(f"Reference: {result['Reference']}")

        # Print model translations in a tabular format
        model_translations = []
        for model_name in model_paths.keys():
            model_translations.append([model_name, result.get(model_name, "N/A")])

        print(tabulate(model_translations, headers=["Model", "Translation"], tablefmt="grid"))
        print("\n" + "-"*80 + "\n")

    print("Translation comparison completed!")

if __name__ == "__main__":
    main()

Using device: cuda

Processing example 1/6
Translating with Base mBART...
Loading model from facebook/mbart-large-50-many-to-many-mmt...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with LoRA Alpha 8...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization1...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with LoRA Alpha 32...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization2...


...

Translating with LoRA Alpha 128...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization4...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with LoRA Alpha 512...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_alpha_optimization5...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.




=== TRANSLATION COMPARISON ===

Example 1:
Hindi: क्या अद्भुत सवारी होगी!
Reference: What a wonderful ride it will be!
+----------------+--------------------------------------+
| Model          | Translation                          |
+================+======================================+
| Base mBART     | What a ride!                         |
+----------------+--------------------------------------+
| LoRA Alpha 8   | What a wonderful ride!               |
+----------------+--------------------------------------+
| LoRA Alpha 32  | What a wonderful ride that would be! |
+----------------+--------------------------------------+
| LoRA Alpha 64  | What a wonderful ride it will be!    |
+----------------+--------------------------------------+
| LoRA Alpha 128 | What a wonderful ride it will be!    |
+----------------+--------------------------------------+
| LoRA Alpha 512 | What a wonderful ride it will be!    |
+----------------+--------------------------------------+

--------

In [ ]:
import torch
from transformers import MBartForConditionalGeneration, MBartTokenizer
import os
from tabulate import tabulate

# Check for GPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Hindi test sentences with English reference translations
test_data = [
    {
        "hindi": "राधा ने कपड़े धोए और प्रेस किए।",
        "reference": "Radha washed clothes and ironed them."
    },
    {
        "hindi": "चुटकुले सुनाओ।",
        "reference": "Tell jokes."
    },
    {
        "hindi": "कृपया अपना उल्लू सीधा मत करो।",
        "reference": "Please don't feather your own nest."
    },
    {
        "hindi": "आप तो ईद का चाँद हो गए!",
        "reference": "You have become a rare sight!"
    },
    {
        "hindi": "उस पर्वतारोही को बचा लिया गया था।",
        "reference": "The mountaineer was rescued."
    },
    {
        "hindi": "नेताओं ने मतभेद सुलझाए।",
        "reference": "Leaders resolved differences."
    }
]

# Model paths
model_paths = {
    "Base mBART": "facebook/mbart-large-50-many-to-many-mmt",
    "Module [q_proj, v_proj]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization1",
    "Module [q_proj, k_proj, v_proj, o_proj]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization2",
    "Module [k_proj, v_proj]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3",
    "Module [q_proj, k_proj]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization4",
    "Module [v_proj, o_proj]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization5",
    "Module [q_proj, k_proj, v_proj, o_proj, fc1, fc2]": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization6"
}

def load_model(model_path):
    """Load model from path, using the base tokenizer"""
    print(f"Loading model from {model_path}...")

    # Always load tokenizer from base model
    tokenizer = MBartTokenizer.from_pretrained('facebook/mbart-large-50-many-to-many-mmt')

    # Load model from specified path
    model = MBartForConditionalGeneration.from_pretrained(model_path)
    model.to(device)

    return model, tokenizer

def translate_text(text, model, tokenizer, max_length=100):
    """Translate a single Hindi text to English"""
    tokenizer.src_lang = "hi_IN"  # Hindi
    tokenizer.tgt_lang = "en_XX"  # English

    # Encode Hindi text
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    # Generate translation
    with torch.no_grad():
        translated = model.generate(
            **inputs,
            max_length=max_length,
            forced_bos_token_id=tokenizer.lang_code_to_id["en_XX"]
        )

    # Decode to English
    output = tokenizer.decode(translated[0], skip_special_tokens=True)
    return output

def main():
    results = []

    # Process each test example
    for i, data in enumerate(test_data):
        print(f"\nProcessing example {i+1}/{len(test_data)}")
        hindi_text = data["hindi"]
        reference = data["reference"]

        row = {
            "Hindi": hindi_text,
            "Reference": reference
        }

        # Translate with each model
        for model_name, model_path in model_paths.items():
            print(f"Translating with {model_name}...")
            try:
                # Load model and tokenizer
                model, tokenizer = load_model(model_path)

                # Translate
                translation = translate_text(hindi_text, model, tokenizer)

                # Add to results
                row[model_name] = translation

                # Clear GPU memory
                del model
                torch.cuda.empty_cache() if torch.cuda.is_available() else None

            except Exception as e:
                print(f"Error with {model_name}: {str(e)}")
                row[model_name] = f"ERROR: {str(e)}"

        results.append(row)

    # Display results in a nice table format
    print("\n\n=== TRANSLATION COMPARISON ===\n")

    for i, result in enumerate(results):
        print(f"Example {i+1}:")
        print(f"Hindi: {result['Hindi']}")
        print(f"Reference: {result['Reference']}")

        # Print model translations in a tabular format
        model_translations = []
        for model_name in model_paths.keys():
            model_translations.append([model_name, result.get(model_name, "N/A")])

        print(tabulate(model_translations, headers=["Model", "Translation"], tablefmt="grid"))
        print("\n" + "-"*80 + "\n")

    print("Translation comparison completed!")

if __name__ == "__main__":
    main()

Using device: cuda

Processing example 1/6
Translating with Base mBART...
Loading model from facebook/mbart-large-50-many-to-many-mmt...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with Module [q_proj, v_proj]...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization1...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with Module [q_proj, k_proj, v_proj, o_proj]...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization2...


...

Translating with Module [v_proj, o_proj]...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization5...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Translating with Module [q_proj, k_proj, v_proj, o_proj, fc1, fc2]...
Loading model from /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization6...


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.




=== TRANSLATION COMPARISON ===

Example 1:
Hindi: राधा ने कपड़े धोए और प्रेस किए।
Reference: Radha washed clothes and ironed them.
+---------------------------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| Model                                             | Translation                                                                                                                                                                                                                                                                                                                                                                            |
+====

## **Extended Result Analysis**

In [ ]:
import os
import csv
import torch
import pandas as pd
from collections import defaultdict
from transformers import MBartForConditionalGeneration, MBart50Tokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

import nltk

nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('wordnet')


# Set up
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Model paths
model_paths = {
    "Base mBART": "facebook/mbart-large-50-many-to-many-mmt",
    "Full Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart",
    "LoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3",
    "QLoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
}

# Dataset root
DATASET_ROOT = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
SETS = ["train_set", "validation_set", "test_set"]

# Categories & structure
CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                  "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
VOICE_TYPES = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

TENSES = [
    "simple_present.csv", "simple_past.csv", "simple_future.csv",
    "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
    "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
]

# Load model
def load_model(model_path):
    print(f"Loading model from: {model_path}")
    tokenizer = MBart50Tokenizer.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
    model = MBartForConditionalGeneration.from_pretrained(model_path).to(device)
    print(f"✓ Model loaded successfully")
    return model, tokenizer

# Translate
def translate(text, model, tokenizer, max_length=100):
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    with torch.no_grad():
        output = model.generate(**inputs, max_length=max_length, forced_bos_token_id=tokenizer.lang_code_to_id["en_XX"])
    return tokenizer.decode(output[0], skip_special_tokens=True)

def compute_scores(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return meteor, chrf_score

# Extract key type from path
def get_type(path):
    for t in SENTENCE_TYPES:
        if t in path:
            return t
    for v in VOICE_TYPES:
        if v in path:
            return v
    return "Unknown"

# Count total sentences for progress bar
def count_total_sentences():
    total = 0
    valid_files = []

    print("📊 Counting total sentences for progress tracking...")

    for split in SETS:
        for category in CATEGORIES:
            cat_path = os.path.join(DATASET_ROOT, split, category)
            if not os.path.exists(cat_path):
                continue

            if category in ["Standard Sentences", "Idiomatic Sentences"]:
                subdirs = SENTENCE_TYPES
            else:
                subdirs = VOICE_TYPES

            for sub in subdirs:
                sub_path = os.path.join(cat_path, sub)
                if not os.path.exists(sub_path):
                    continue

                for tense_file in TENSES:
                    csv_path = os.path.join(sub_path, tense_file)
                    if not os.path.exists(csv_path):
                        continue

                    try:
                        df = pd.read_csv(csv_path)
                        sentence_count = len(df)
                        total += sentence_count
                        valid_files.append((csv_path, sentence_count, split, category, sub, tense_file))
                    except Exception as e:
                        print(f"⚠️  Error reading {csv_path}: {e}")

    print(f"📈 Total sentences to process: {total}")
    print(f"📁 Valid CSV files found: {len(valid_files)}")
    return total, valid_files

# Main
def main():
    print("🚀 Starting Translation Model Evaluation")

    # Count total work
    total_sentences, valid_files = count_total_sentences()

    # Load models with progress
    print("\n🔄 Loading models...")
    models = {}
    for name, path in tqdm(model_paths.items(), desc="Loading models", unit="model"):
        try:
            models[name] = load_model(path)
        except Exception as e:
            print(f"❌ Failed to load {name}: {e}")
            continue

    print(f"✅ Successfully loaded {len(models)} models")

    # Initialize aggregation
    aggregate_scores = {model: defaultdict(lambda: {"meteor": [], "chrf": []}) for model in models}

    # Process with progress bars
    total_operations = total_sentences * len(models)
    print(f"\n📊 Total operations to perform: {total_operations:,}")

    # Main progress bar for overall completion
    main_pbar = tqdm(total=total_operations, desc="Overall Progress", unit="translations")

    sentences_processed = 0
    files_processed = 0

    for file_info in tqdm(valid_files, desc="Processing files", unit="file", position=1, leave=False):
        csv_path, sentence_count, split, category, sub, tense_file = file_info
        files_processed += 1

        # Debug info for current file
        current_file_desc = f"[{files_processed}/{len(valid_files)}] {category}/{sub}/{tense_file}"
        tqdm.write(f"🔍 Processing: {current_file_desc}")

        try:
            df = pd.read_csv(csv_path)

            # Process each sentence in the file
            for row_idx, row in tqdm(df.iterrows(),
                                   total=len(df),
                                   desc=f"Sentences in {tense_file}",
                                   unit="sent",
                                   position=2,
                                   leave=False):

                src = str(row["Hindi_Text"])
                ref = str(row["English_Text"])
                sentences_processed += 1

                # Debug: Show current sentence being processed
                if sentences_processed % 100 == 0:  # Every 100th sentence
                    tqdm.write(f"🔤 Sample sentence {sentences_processed}: {src[:50]}...")

                # Process with each model
                for model_idx, (model_name, (model, tokenizer)) in enumerate(models.items()):
                    try:
                        # Translate
                        start_time = time.time()
                        pred = translate(src, model, tokenizer)
                        translation_time = time.time() - start_time

                        # Compute scores
                        meteor, chrf = compute_scores(ref, pred)

                        # Aggregate by category
                        aggregate_scores[model_name][f"Category::{category}"]["meteor"].append(meteor)
                        aggregate_scores[model_name][f"Category::{category}"]["chrf"].append(chrf)

                        # Aggregate by sentence/voice type
                        type_key = get_type(sub)
                        aggregate_scores[model_name][f"Type::{type_key}"]["meteor"].append(meteor)
                        aggregate_scores[model_name][f"Type::{type_key}"]["chrf"].append(chrf)

                        # Aggregate by tense
                        tense_key = f"Tense::{tense_file.replace('.csv','')}"
                        aggregate_scores[model_name][tense_key]["meteor"].append(meteor)
                        aggregate_scores[model_name][tense_key]["chrf"].append(chrf)

                        # Debug: Show occasional translation results
                        if sentences_processed % 500 == 0:  # Every 500th sentence
                            tqdm.write(f"🔄 {model_name} translation time: {translation_time:.3f}s")
                            tqdm.write(f"📝 SRC: {src[:50]}...")
                            tqdm.write(f"🎯 REF: {ref[:50]}...")
                            tqdm.write(f"🤖 PRED: {pred[:50]}...")
                            tqdm.write(f"📊 METEOR: {meteor:.4f}, CHRF: {chrf:.4f}")
                            tqdm.write("─" * 50)

                        main_pbar.update(1)

                    except Exception as e:
                        tqdm.write(f"❌ Error with {model_name} on sentence {sentences_processed}: {str(e)[:100]}")
                        main_pbar.update(1)
                        continue

        except Exception as e:
            tqdm.write(f"❌ Error processing file {csv_path}: {e}")
            # Still update progress bar for the sentences we couldn't process
            main_pbar.update(sentence_count * len(models))
            continue

    main_pbar.close()

    # Print Results
    print(f"\n🎉 Processing complete! Processed {sentences_processed:,} sentences across {len(models)} models")
    print("=" * 80)

    for model_name in aggregate_scores:
        print(f"\n===== 📊 {model_name} RESULTS =====")

        # Sort results by category type for better organization
        sorted_keys = sorted(aggregate_scores[model_name].keys())

        for key in sorted_keys:
            scores = aggregate_scores[model_name][key]
            if scores["meteor"]:  # Only show if we have data
                avg_meteor = sum(scores["meteor"]) / len(scores["meteor"])
                avg_chrf = sum(scores["chrf"]) / len(scores["chrf"])
                sample_count = len(scores["meteor"])
                print(f"{key:<40} | METEOR: {avg_meteor:.4f} | CHRF: {avg_chrf:.4f} | Samples: {sample_count:,}")
            else:
                print(f"{key:<40} | No data available")

    print(f"\n✅ Evaluation completed successfully!")

if __name__ == "__main__":
    main()

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
🚀 Starting Translation Model Evaluation
📊 Counting total sentences for progress tracking...
📈 Total sentences to process: 10085
📁 Valid CSV files found: 477

🔄 Loading models...


Loading models:   0%|          | 0/4 [00:00<?, ?model/s]

Loading model from: facebook/mbart-large-50-many-to-many-mmt


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


...

🔍 Processing: [476/477] Voice and Speech Constructions/Indirect Speech/past_perfect.csv




Overall Progress: 100%|█████████▉| 40224/40340 [3:27:01<00:59,  1.96translations/s]

Overall Progress: 100%|█████████▉| 40228/40340 [3:27:03<00:48,  2.32translations/s]

Overall Progress: 100%|█████████▉| 40232/40340 [3:27:04<00:35,  3.07translations/s]

Overall Progress: 100%|█████████▉| 40236/40340 [3:27:06<00:38,  2.67translations/s]

Overall Progress: 100%|█████████▉| 40240/40340 [3:27:07<00:33,  2.97translations/s]

Overall Progress: 100%|█████████▉| 40244/40340 [3:27:08<00:28,  3.43translations/s]

Overall Progress: 100%|█████████▉| 40248/40340 [3:27:09<00:28,  3.20translations/s]

Overall Progress: 100%|█████████▉| 40252/40340 [3:27:11<00:36,  2.40translations/s]

Overall Progress: 100%|█████████▉| 40256/40340 [3:27:13<00:38,  2.16translations/s]

Overall Progress: 100%|█████████▉| 40260/40340 [3:27:14<00:30,  2.63translations/s]

Overall Progress: 100%|█████████▉| 40264/40340 [3:27:16<00:29,  2.59translations/s]

Overall Progress: 100%|█████████▉| 40268/40340 [3:27:17<00:24, 

🔍 Processing: [477/477] Voice and Speech Constructions/Indirect Speech/future_perfect.csv




Overall Progress: 100%|█████████▉| 40284/40340 [3:27:22<00:18,  2.99translations/s]

Overall Progress: 100%|█████████▉| 40288/40340 [3:27:24<00:19,  2.72translations/s]

Overall Progress: 100%|█████████▉| 40292/40340 [3:27:25<00:16,  2.84translations/s]

Overall Progress: 100%|█████████▉| 40296/40340 [3:27:27<00:18,  2.36translations/s]

Overall Progress: 100%|█████████▉| 40300/40340 [3:27:28<00:15,  2.55translations/s]

Overall Progress: 100%|█████████▉| 40304/40340 [3:27:30<00:15,  2.32translations/s]

Overall Progress: 100%|█████████▉| 40308/40340 [3:27:32<00:12,  2.57translations/s]

Overall Progress: 100%|█████████▉| 40312/40340 [3:27:33<00:10,  2.69translations/s]

Overall Progress: 100%|█████████▉| 40316/40340 [3:27:34<00:09,  2.64translations/s]

Overall Progress: 100%|█████████▉| 40320/40340 [3:27:36<00:06,  2.99translations/s]

Overall Progress: 100%|█████████▉| 40324/40340 [3:27:37<00:04,  3.31translations/s]

Overall Progress: 100%|█████████▉| 40328/40340 [3:27:39<00:05, 


🎉 Processing complete! Processed 10,085 sentences across 4 models

===== 📊 Base mBART RESULTS =====
Category::Idiomatic Sentences            | METEOR: 0.4666 | CHRF: 0.3869 | Samples: 3,154
Category::Standard Sentences             | METEOR: 0.7313 | CHRF: 0.6685 | Samples: 3,331
Category::Voice and Speech Constructions | METEOR: 0.7997 | CHRF: 0.7496 | Samples: 3,600
Tense::future_continuous                 | METEOR: 0.6637 | CHRF: 0.5926 | Samples: 1,097
Tense::future_perfect                    | METEOR: 0.6159 | CHRF: 0.5393 | Samples: 1,093
Tense::past_continuous                   | METEOR: 0.6735 | CHRF: 0.6212 | Samples: 1,106
Tense::past_perfect                      | METEOR: 0.6470 | CHRF: 0.5825 | Samples: 1,096
Tense::present_continuous                | METEOR: 0.6162 | CHRF: 0.5697 | Samples: 1,101
Tense::present_perfect                   | METEOR: 0.7320 | CHRF: 0.6690 | Samples: 1,093
Tense::simple_future                     | METEOR: 0.7385 | CHRF: 0.6693 | Samples: 1,113

## **Idioms only LoRA**

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_idioms_from_directory(base_path):
    """Load only idiomatic sentences from the dataset structure"""
    data = {'train': [], 'validation': [], 'test': []}

    # Dataset structure mapping
    set_mappings = {
        'train': 'train_set',
        'validation': 'validation_set',
        'test': 'test_set'
    }

    # Sentence types and tense files
    SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                      "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]

    TENSES = [
        "simple_present.csv", "simple_past.csv", "simple_future.csv",
        "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
        "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
    ]

    print("Loading idiomatic sentences from dataset...")

    for split, folder_name in set_mappings.items():
        split_path = os.path.join(base_path, folder_name, "Idiomatic Sentences")

        if not os.path.exists(split_path):
            print(f"Warning: Path {split_path} does not exist")
            continue

        print(f"Processing {split} split...")

        for sentence_type in SENTENCE_TYPES:
            sentence_type_path = os.path.join(split_path, sentence_type)

            if not os.path.exists(sentence_type_path):
                continue

            for tense_file in TENSES:
                csv_path = os.path.join(sentence_type_path, tense_file)

                if not os.path.exists(csv_path):
                    continue

                try:
                    df = pd.read_csv(csv_path)
                    hindi_sentences = df['Hindi_Text'].tolist()
                    english_sentences = df['English_Text'].tolist()
                    data[split].extend(zip(hindi_sentences, english_sentences))
                    print(f"  Loaded {len(df)} sentences from {sentence_type}/{tense_file}")
                except Exception as e:
                    print(f"  Error loading {csv_path}: {e}")

    print(f"Total idioms loaded - Train: {len(data['train'])}, Validation: {len(data['validation'])}, Test: {len(data['test'])}")
    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()

    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    return model, tokenizer, gpu_increase

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=1024,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)
    model.to(device)

    timer_callback = TimerCallback()

    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        # weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=3e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    # Calculate GPU memory usage after training
    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    # Save the model directly to Google Drive
    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_idioms_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)

    return model, gpu_increase, avg_epoch_time

@torch.no_grad()
def translate_with_model(text, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)

    start_time = time.time()
    translated = model.generate(**inputs, max_length=max_length)
    inference_time = time.time() - start_time

    return tokenizer.batch_decode(translated, skip_special_tokens=True)[0], inference_time

def calculate_metrics(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return {'meteor': meteor, 'chrf': chrf_score}

def evaluate_model_on_idioms(model, tokenizer, test_data):
    """Evaluate model specifically on idiomatic sentences"""
    print(f"Evaluating model on {len(test_data)} idiomatic sentences...")
    all_scores = {metric: [] for metric in ['meteor', 'chrf']}

    for hindi, english in tqdm(test_data, desc="Evaluating idioms"):
        translation, _ = translate_with_model(hindi, model, tokenizer)
        scores = calculate_metrics(english, translation)
        for metric, score in scores.items():
            all_scores[metric].append(score)

    metrics = {metric: sum(scores) / len(scores) for metric, scores in all_scores.items()}
    return metrics

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory = load_model()

    print("Loading idiomatic sentences from directory.")
    # Update this path to match your dataset structure
    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
    idioms_data = load_idioms_from_directory(base_path)

    # Check if we have idioms data
    if not idioms_data['train'] or not idioms_data['validation'] or not idioms_data['test']:
        print("Warning: Some splits have no idiomatic data. Please check your dataset path and structure.")
        exit(1)

    print("Preparing datasets for idiomatic sentences.")
    train_dataset = prepare_dataset(idioms_data['train'], tokenizer)
    val_dataset = prepare_dataset(idioms_data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA on idiomatic sentences.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model on idiomatic sentences.")
    test_idioms = idioms_data['test']
    evaluation_results = evaluate_model_on_idioms(fine_tuned_model, tokenizer, test_idioms)

    # Only keep the requested metrics
    metrics = {
        'original_model_gpu_memory_mb': original_model_memory,
        'lora_fine_tuned_model_additional_gpu_memory_mb': lora_memory_increase,
        'avg_training_time_per_epoch_sec': avg_epoch_time,
        'meteor_score': evaluation_results['meteor'],
        'chrf_score': evaluation_results['chrf']
    }

    results_df = pd.DataFrame([metrics])
    results_df.index = ['Idioms_LoRA_Results']

    print("\nSummary of Results for LoRA Fine-tuned mBART on Idiomatic Sentences:")
    print(results_df.to_string())

    # Save results CSV directly to Google Drive
    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_idioms_fine_tuned_mbart_performance.csv"
    results_df.to_csv(drive_csv_path)
    print(f"Results have been saved to Google Drive: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Original mBART model GPU memory usage: 2332.04 MB
Loading idiomatic sentences from directory.
Loading idiomatic sentences from dataset...
Processing train split...
  Loaded 35 sentences from Declarative Sentences/simple_present.csv
  Loaded 35 sentences from Declarative Sentences/simple_past.csv
  Loaded 35 sentences from Declarative Sentences/simple_future.csv
  Loaded 35 sentences from Declarative Sentences/present_continuous.csv
  Loaded 35 sentences from Declarative Sentences/past_continuous.csv
  Loaded 35 sentences from Declarative Sentences/future_continuous.csv
  Loaded 35 sentences from Declarative Sentences/present_perfect.csv
  Loaded 35 sentences from Declarative Sentences/past_perfect.csv
  Loaded 35 sentences from Declarative Sentences/future_perfect.csv
  Loaded 35 sentences from Exclamatory Sentences/simple_present.csv
  Loaded 35 sentences from Exclamatory Sentences/simple_past.csv
  Loaded 35 sentences from Exclamatory Sentences/simple_future.csv
  Loaded 35 sentences

Map (num_proc=2):   0%|          | 0/2208 [00:00<?, ? examples/s]

...

Fine-tuning the model with LoRA on idiomatic sentences.


No label_names provided for model class `PeftModelForSeq2SeqLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


Epoch 1.0 took 88.56 seconds
Epoch 2.0 took 86.03 seconds
Epoch 3.0 took 74.46 seconds
Epoch 4.0 took 74.34 seconds
Epoch 5.0 took 74.05 seconds
LoRA fine-tuned model additional GPU memory usage after training: -2331.27 MB
Model saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_idioms_fine_tuned_mbart
Evaluating the model on idiomatic sentences.
Evaluating model on 469 idiomatic sentences...


Evaluating idioms: 100%|██████████| 469/469 [03:09<00:00,  2.47it/s]


Summary of Results for LoRA Fine-tuned mBART on Idiomatic Sentences:
                     original_model_gpu_memory_mb  lora_fine_tuned_model_additional_gpu_memory_mb  avg_training_time_per_epoch_sec  meteor_score  chrf_score
Idioms_LoRA_Results                   2332.036133                                    -2331.274414                        79.487261      0.641621    0.542492
Results have been saved to Google Drive: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_idioms_fine_tuned_mbart_performance.csv


## **Top and Worst Performers**

In [ ]:
import os
import csv
import torch
import pandas as pd
from collections import defaultdict
from transformers import MBartForConditionalGeneration, MBart50Tokenizer
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time
import json

import nltk

nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('wordnet')


# Set up
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Model paths
model_paths = {
    "Base mBART": "facebook/mbart-large-50-many-to-many-mmt",
    "Full Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/Full fine-tune/full_fine_tuned_mbart",
    "LoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_fine_tuned_mbart_module_optimization3",
    "QLoRA Fine-tuned": "/content/drive/MyDrive/Colab Notebooks/Translation Models/qlora_fine_tuned_mbart"
}

# Dataset root
DATASET_ROOT = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
SETS = ["train_set", "validation_set", "test_set"]

# Categories & structure
CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                  "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
VOICE_TYPES = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

TENSES = [
    "simple_present.csv", "simple_past.csv", "simple_future.csv",
    "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
    "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
]

# Load model
def load_model(model_path):
    print(f"Loading model from: {model_path}")
    tokenizer = MBart50Tokenizer.from_pretrained("facebook/mbart-large-50-many-to-many-mmt")
    model = MBartForConditionalGeneration.from_pretrained(model_path).to(device)
    print(f"✓ Model loaded successfully")
    return model, tokenizer

# Translate
def translate(text, model, tokenizer, max_length=100):
    tokenizer.src_lang = "hi_IN"
    tokenizer.tgt_lang = "en_XX"
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    with torch.no_grad():
        output = model.generate(**inputs, max_length=max_length, forced_bos_token_id=tokenizer.lang_code_to_id["en_XX"])
    return tokenizer.decode(output[0], skip_special_tokens=True)

def compute_scores(reference, candidate):
    reference_tokens = nltk.word_tokenize(reference.lower())
    candidate_tokens = nltk.word_tokenize(candidate.lower())
    meteor = meteor_score([reference_tokens], candidate_tokens)
    chrf = CHRF()
    chrf_score = chrf.sentence_score(candidate, [reference]).score / 100
    return meteor, chrf_score

# Extract key type from path
def get_type(path):
    for t in SENTENCE_TYPES:
        if t in path:
            return t
    for v in VOICE_TYPES:
        if v in path:
            return v
    return "Unknown"

# Count total sentences for progress bar
def count_total_sentences():
    total = 0
    valid_files = []

    print("📊 Counting total sentences for progress tracking...")

    for split in SETS:
        for category in CATEGORIES:
            cat_path = os.path.join(DATASET_ROOT, split, category)
            if not os.path.exists(cat_path):
                continue

            if category in ["Standard Sentences", "Idiomatic Sentences"]:
                subdirs = SENTENCE_TYPES
            else:
                subdirs = VOICE_TYPES

            for sub in subdirs:
                sub_path = os.path.join(cat_path, sub)
                if not os.path.exists(sub_path):
                    continue

                for tense_file in TENSES:
                    csv_path = os.path.join(sub_path, tense_file)
                    if not os.path.exists(csv_path):
                        continue

                    try:
                        df = pd.read_csv(csv_path)
                        sentence_count = len(df)
                        total += sentence_count
                        valid_files.append((csv_path, sentence_count, split, category, sub, tense_file))
                    except Exception as e:
                        print(f"⚠️  Error reading {csv_path}: {e}")

    print(f"📈 Total sentences to process: {total}")
    print(f"📁 Valid CSV files found: {len(valid_files)}")
    return total, valid_files

def calculate_lora_advantage(sentence_data):
    """Calculate how much better LoRA/QLoRA performs compared to Full Fine-tuned"""
    full_meteor = sentence_data.get("Full Fine-tuned", {}).get("meteor", 0)
    lora_meteor = sentence_data.get("LoRA Fine-tuned", {}).get("meteor", 0)
    qlora_meteor = sentence_data.get("QLoRA Fine-tuned", {}).get("meteor", 0)

    # Calculate advantage (positive means LoRA/QLoRA is better)
    lora_advantage = lora_meteor - full_meteor
    qlora_advantage = qlora_meteor - full_meteor

    # Use the best of LoRA or QLoRA
    best_advantage = max(lora_advantage, qlora_advantage)
    best_method = "LoRA Fine-tuned" if lora_advantage >= qlora_advantage else "QLoRA Fine-tuned"

    return best_advantage, best_method, lora_advantage, qlora_advantage

def print_sentence_analysis(category_sentences, category_name, analysis_type):
    """Print detailed analysis of best/worst sentences"""
    print(f"\n{'='*80}")
    print(f"📊 {analysis_type.upper()} PERFORMING SENTENCES - {category_name}")
    print(f"{'='*80}")

    for i, (advantage, method, sentence_data) in enumerate(category_sentences, 1):
        print(f"\n🏆 RANK #{i}")
        print(f"━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━")

        # Show the advantage
        direction = "better" if advantage > 0 else "worse"
        print(f"📈 {method} is {abs(advantage):.4f} METEOR points {direction} than Full Fine-tuned")

        # Show source and reference
        print(f"🔤 HINDI (Source): {sentence_data['source']}")
        print(f"🎯 REFERENCE: {sentence_data['reference']}")
        print(f"📍 CONTEXT: {sentence_data['file_info']}")

        # Show all model outputs and scores
        print(f"\n📊 MODEL COMPARISONS:")
        for model_name in ["Base mBART", "Full Fine-tuned", "LoRA Fine-tuned", "QLoRA Fine-tuned"]:
            if model_name in sentence_data:
                data = sentence_data[model_name]
                meteor_score = data['meteor']
                chrf_score = data['chrf']
                translation = data['translation']

                # Highlight the best performing models
                if model_name in ["LoRA Fine-tuned", "QLoRA Fine-tuned"]:
                    print(f"  🌟 {model_name}:")
                else:
                    print(f"  📝 {model_name}:")

                print(f"     Translation: {translation}")
                print(f"     METEOR: {meteor_score:.4f} | CHRF: {chrf_score:.4f}")

        # Show specific LoRA vs Full comparison
        lora_data = sentence_data.get("LoRA Fine-tuned", {})
        qlora_data = sentence_data.get("QLoRA Fine-tuned", {})
        full_data = sentence_data.get("Full Fine-tuned", {})

        if lora_data and full_data:
            lora_diff = lora_data['meteor'] - full_data['meteor']
            print(f"\n💡 LoRA vs Full Fine-tuned: {lora_diff:+.4f} METEOR points")

        if qlora_data and full_data:
            qlora_diff = qlora_data['meteor'] - full_data['meteor']
            print(f"💡 QLoRA vs Full Fine-tuned: {qlora_diff:+.4f} METEOR points")

# Main
def main():
    print("🚀 Starting Translation Model Evaluation - Focus on LoRA vs Full Fine-tuning")

    # Count total work
    total_sentences, valid_files = count_total_sentences()

    # Load models with progress
    print("\n🔄 Loading models...")
    models = {}
    for name, path in tqdm(model_paths.items(), desc="Loading models", unit="model"):
        try:
            models[name] = load_model(path)
        except Exception as e:
            print(f"❌ Failed to load {name}: {e}")
            continue

    print(f"✅ Successfully loaded {len(models)} models")

    # Initialize aggregation and sentence tracking
    aggregate_scores = {model: defaultdict(lambda: {"meteor": [], "chrf": []}) for model in models}

    # Track individual sentences for each category
    category_sentences = {category: [] for category in CATEGORIES}

    # Process with progress bars
    total_operations = total_sentences * len(models)
    print(f"\n📊 Total operations to perform: {total_operations:,}")

    # Main progress bar for overall completion
    main_pbar = tqdm(total=total_operations, desc="Overall Progress", unit="translations")

    sentences_processed = 0
    files_processed = 0

    for file_info in tqdm(valid_files, desc="Processing files", unit="file", position=1, leave=False):
        csv_path, sentence_count, split, category, sub, tense_file = file_info
        files_processed += 1

        # Debug info for current file
        current_file_desc = f"[{files_processed}/{len(valid_files)}] {category}/{sub}/{tense_file}"
        tqdm.write(f"🔍 Processing: {current_file_desc}")

        try:
            df = pd.read_csv(csv_path)

            # Process each sentence in the file
            for row_idx, row in tqdm(df.iterrows(),
                                   total=len(df),
                                   desc=f"Sentences in {tense_file}",
                                   unit="sent",
                                   position=2,
                                   leave=False):

                src = str(row["Hindi_Text"])
                ref = str(row["English_Text"])
                sentences_processed += 1

                # Track this sentence's performance across all models
                sentence_data = {
                    'source': src,
                    'reference': ref,
                    'file_info': f"{split}/{category}/{sub}/{tense_file}",
                    'category': category
                }

                # Debug: Show current sentence being processed
                if sentences_processed % 100 == 0:  # Every 100th sentence
                    tqdm.write(f"🔤 Sample sentence {sentences_processed}: {src[:50]}...")

                # Process with each model
                for model_idx, (model_name, (model, tokenizer)) in enumerate(models.items()):
                    try:
                        # Translate
                        start_time = time.time()
                        pred = translate(src, model, tokenizer)
                        translation_time = time.time() - start_time

                        # Compute scores
                        meteor, chrf = compute_scores(ref, pred)

                        # Store individual sentence data
                        sentence_data[model_name] = {
                            'translation': pred,
                            'meteor': meteor,
                            'chrf': chrf,
                            'time': translation_time
                        }

                        # Aggregate by category
                        aggregate_scores[model_name][f"Category::{category}"]["meteor"].append(meteor)
                        aggregate_scores[model_name][f"Category::{category}"]["chrf"].append(chrf)

                        # Aggregate by sentence/voice type
                        type_key = get_type(sub)
                        aggregate_scores[model_name][f"Type::{type_key}"]["meteor"].append(meteor)
                        aggregate_scores[model_name][f"Type::{type_key}"]["chrf"].append(chrf)

                        # Aggregate by tense
                        tense_key = f"Tense::{tense_file.replace('.csv','')}"
                        aggregate_scores[model_name][tense_key]["meteor"].append(meteor)
                        aggregate_scores[model_name][tense_key]["chrf"].append(chrf)

                        # Debug: Show occasional translation results
                        if sentences_processed % 500 == 0:  # Every 500th sentence
                            tqdm.write(f"🔄 {model_name} translation time: {translation_time:.3f}s")
                            tqdm.write(f"📝 SRC: {src[:50]}...")
                            tqdm.write(f"🎯 REF: {ref[:50]}...")
                            tqdm.write(f"🤖 PRED: {pred[:50]}...")
                            tqdm.write(f"📊 METEOR: {meteor:.4f}, CHRF: {chrf:.4f}")
                            tqdm.write("─" * 50)

                        main_pbar.update(1)

                    except Exception as e:
                        tqdm.write(f"❌ Error with {model_name} on sentence {sentences_processed}: {str(e)[:100]}")
                        main_pbar.update(1)
                        continue

                # After processing all models for this sentence, calculate LoRA advantage
                if len(sentence_data) > 4:  # Has all model results + metadata
                    advantage, best_method, lora_adv, qlora_adv = calculate_lora_advantage(sentence_data)
                    category_sentences[category].append((advantage, best_method, sentence_data.copy()))

        except Exception as e:
            tqdm.write(f"❌ Error processing file {csv_path}: {e}")
            # Still update progress bar for the sentences we couldn't process
            main_pbar.update(sentence_count * len(models))
            continue

    main_pbar.close()

    # Sort sentences by LoRA advantage for each category
    print(f"\n🔄 Analyzing sentence performance...")
    for category in CATEGORIES:
        if category_sentences[category]:
            # Sort by advantage (best LoRA/QLoRA advantage first, worst last)
            category_sentences[category].sort(key=lambda x: x[0], reverse=True)
            print(f"📊 {category}: {len(category_sentences[category])} sentences analyzed")

    # Print aggregate results first
    print(f"\n🎉 Processing complete! Processed {sentences_processed:,} sentences across {len(models)} models")
    print("=" * 80)
    print("📊 OVERALL AGGREGATE RESULTS")
    print("=" * 80)

    for model_name in aggregate_scores:
        print(f"\n===== 📊 {model_name} RESULTS =====")

        # Sort results by category type for better organization
        sorted_keys = sorted(aggregate_scores[model_name].keys())

        for key in sorted_keys:
            scores = aggregate_scores[model_name][key]
            if scores["meteor"]:  # Only show if we have data
                avg_meteor = sum(scores["meteor"]) / len(scores["meteor"])
                avg_chrf = sum(scores["chrf"]) / len(scores["chrf"])
                sample_count = len(scores["meteor"])
                print(f"{key:<40} | METEOR: {avg_meteor:.4f} | CHRF: {avg_chrf:.4f} | Samples: {sample_count:,}")
            else:
                print(f"{key:<40} | No data available")

    # Print detailed sentence analysis
    print(f"\n" + "="*100)
    print("🎯 DETAILED SENTENCE ANALYSIS: LoRA/QLoRA vs Full Fine-tuning")
    print("="*100)

    for category in CATEGORIES:
        if not category_sentences[category]:
            continue

        # Get top 20 best (where LoRA/QLoRA outperforms Full Fine-tuned the most)
        best_sentences = category_sentences[category][:20]

        # Get top 20 worst (where LoRA/QLoRA underperforms Full Fine-tuned the most)
        worst_sentences = category_sentences[category][-20:]
        worst_sentences.reverse()  # Show worst first

        # Print analysis
        print_sentence_analysis(best_sentences, category, "BEST")
        print_sentence_analysis(worst_sentences, category, "WORST")

        # Summary statistics for this category
        advantages = [x[0] for x in category_sentences[category]]
        positive_advantages = [x for x in advantages if x > 0]
        negative_advantages = [x for x in advantages if x < 0]

        print(f"\n📈 SUMMARY FOR {category}:")
        print(f"   Total sentences: {len(advantages)}")
        print(f"   LoRA/QLoRA better: {len(positive_advantages)} ({len(positive_advantages)/len(advantages)*100:.1f}%)")
        print(f"   Full Fine-tuned better: {len(negative_advantages)} ({len(negative_advantages)/len(advantages)*100:.1f}%)")
        if advantages:
            print(f"   Average advantage: {sum(advantages)/len(advantages):+.4f} METEOR points")
            print(f"   Best advantage: {max(advantages):+.4f} METEOR points")
            print(f"   Worst disadvantage: {min(advantages):+.4f} METEOR points")

    print(f"\n✅ Analysis completed! LoRA/QLoRA comparison with Full Fine-tuning ready.")

if __name__ == "__main__":
    main()

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Using device: cuda
🚀 Starting Translation Model Evaluation - Focus on LoRA vs Full Fine-tuning
📊 Counting total sentences for progress tracking...
📈 Total sentences to process: 10085
📁 Valid CSV files found: 477

🔄 Loading models...


Loading models:   0%|          | 0/4 [00:00<?, ?model/s]

Loading model from: facebook/mbart-large-50-many-to-many-mmt


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


...

🔍 Processing: [476/477] Voice and Speech Constructions/Indirect Speech/past_perfect.csv




Overall Progress: 100%|█████████▉| 40224/40340 [3:29:35<00:51,  2.26translations/s]

Overall Progress: 100%|█████████▉| 40228/40340 [3:29:37<00:46,  2.39translations/s]

Overall Progress: 100%|█████████▉| 40232/40340 [3:29:38<00:37,  2.84translations/s]

Overall Progress: 100%|█████████▉| 40236/40340 [3:29:40<00:45,  2.26translations/s]

Overall Progress: 100%|█████████▉| 40240/40340 [3:29:41<00:37,  2.67translations/s]

Overall Progress: 100%|█████████▉| 40244/40340 [3:29:42<00:29,  3.28translations/s]

Overall Progress: 100%|█████████▉| 40248/40340 [3:29:44<00:29,  3.12translations/s]

Overall Progress: 100%|█████████▉| 40252/40340 [3:29:45<00:37,  2.35translations/s]

Overall Progress: 100%|█████████▉| 40256/40340 [3:29:47<00:34,  2.42translations/s]

Overall Progress: 100%|█████████▉| 40260/40340 [3:29:48<00:24,  3.21translations/s]

Overall Progress: 100%|█████████▉| 40264/40340 [3:29:50<00:28,  2.68translations/s]

Overall Progress: 100%|█████████▉| 40268/40340 [3:29:51<00:26, 

🔍 Processing: [477/477] Voice and Speech Constructions/Indirect Speech/future_perfect.csv




Overall Progress: 100%|█████████▉| 40284/40340 [3:29:57<00:18,  2.98translations/s]

Overall Progress: 100%|█████████▉| 40288/40340 [3:29:58<00:19,  2.63translations/s]

Overall Progress: 100%|█████████▉| 40292/40340 [3:30:00<00:16,  2.99translations/s]

Overall Progress: 100%|█████████▉| 40296/40340 [3:30:01<00:15,  2.79translations/s]

Overall Progress: 100%|█████████▉| 40300/40340 [3:30:03<00:15,  2.65translations/s]

Overall Progress: 100%|█████████▉| 40304/40340 [3:30:04<00:17,  2.11translations/s]

Overall Progress: 100%|█████████▉| 40308/40340 [3:30:06<00:15,  2.06translations/s]

Overall Progress: 100%|█████████▉| 40312/40340 [3:30:08<00:11,  2.46translations/s]

Overall Progress: 100%|█████████▉| 40316/40340 [3:30:09<00:09,  2.54translations/s]

Overall Progress: 100%|█████████▉| 40320/40340 [3:30:11<00:06,  2.94translations/s]

Overall Progress: 100%|█████████▉| 40324/40340 [3:30:12<00:04,  3.21translations/s]

Overall Progress: 100%|█████████▉| 40328/40340 [3:30:13<00:04, 


🔄 Analyzing sentence performance...
📊 Standard Sentences: 3331 sentences analyzed
📊 Idiomatic Sentences: 3154 sentences analyzed
📊 Voice and Speech Constructions: 3600 sentences analyzed

🎉 Processing complete! Processed 10,085 sentences across 4 models
📊 OVERALL AGGREGATE RESULTS

===== 📊 Base mBART RESULTS =====
Category::Idiomatic Sentences            | METEOR: 0.4666 | CHRF: 0.3869 | Samples: 3,154
Category::Standard Sentences             | METEOR: 0.7313 | CHRF: 0.6685 | Samples: 3,331
Category::Voice and Speech Constructions | METEOR: 0.7997 | CHRF: 0.7496 | Samples: 3,600
Tense::future_continuous                 | METEOR: 0.6637 | CHRF: 0.5926 | Samples: 1,097
Tense::future_perfect                    | METEOR: 0.6159 | CHRF: 0.5393 | Samples: 1,093
Tense::past_continuous                   | METEOR: 0.6735 | CHRF: 0.6212 | Samples: 1,106
Tense::past_perfect                      | METEOR: 0.6470 | CHRF: 0.5825 | Samples: 1,096
Tense::present_continuous                | METEOR: 0.

## **LoRA + Partial Unfreezing**

In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_full_dataset(base_path):
    """Load dataset and include category info for test set"""
    data = {'train': [], 'validation': [], 'test': []}

    set_mappings = {
        'train': 'train_set',
        'validation': 'validation_set',
        'test': 'test_set'
    }

    CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
    SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                      "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
    TENSES = [
        "simple_present.csv", "simple_past.csv", "simple_future.csv",
        "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
        "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
    ]

    print("Loading full dataset...")

    for split, folder_name in set_mappings.items():
        for category in CATEGORIES:
            split_path = os.path.join(base_path, folder_name, category)

            if not os.path.exists(split_path):
                print(f"Warning: Path {split_path} does not exist")
                continue

            print(f"Processing {split} split - {category}...")

            if category != "Voice and Speech Constructions":
                for sentence_type in SENTENCE_TYPES:
                    sentence_type_path = os.path.join(split_path, sentence_type)

                    if not os.path.exists(sentence_type_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(sentence_type_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{sentence_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")
            else:
                # Voice and Speech Constructions have different subtypes
                voice_types = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

                for voice_type in voice_types:
                    voice_path = os.path.join(split_path, voice_type)
                    if not os.path.exists(voice_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(voice_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{voice_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")


    print(f"Total loaded - Train: {len(data['train'])}, Validation: {len(data['validation'])}, Test: {len(data['test'])}")
    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    return model, tokenizer, gpu_increase

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def get_named_layer_groups(model):
    groups = {
        "embeddings": [],
        "encoder_layers": {},   # encoder_layers[layer_num]
        "decoder_layers": {},   # decoder_layers[layer_num]
        "lm_head": [],
        "decoder_layernorm": [],
        "other": []
    }

    for name, param in model.named_parameters():
        parts = name.split('.')

        if 'embed' in name:
            groups["embeddings"].append(param)

        elif 'encoder.layers' in name:
            # find index of 'layers' in parts
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["encoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                # fallback: put in 'other'
                groups["other"].append(param)

        elif 'decoder.layers' in name:
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["decoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                groups["other"].append(param)

        elif 'lm_head' in name:
            groups["lm_head"].append(param)

        elif 'decoder.layernorm_embedding' in name:
            groups["decoder_layernorm"].append(param)

        else:
            groups["other"].append(param)

    return groups

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)

    TOP_N = 1  # Unfreeze top N encoder & decoder layers

    # Get semantically grouped layers
    layer_groups = get_named_layer_groups(model)

    # # Step 1: Freeze everything
    # for param in model.parameters():
    #     param.requires_grad = False

    # Step 2: Unfreeze top N encoder layers
    encoder_layer_ids = sorted(layer_groups["encoder_layers"].keys())[-TOP_N:]
    for i in encoder_layer_ids:
        for param in layer_groups["encoder_layers"][i]:
            param.requires_grad = True

    # Step 3: Unfreeze top N decoder layers
    decoder_layer_ids = sorted(layer_groups["decoder_layers"].keys())[-TOP_N:]
    for i in decoder_layer_ids:
        for param in layer_groups["decoder_layers"][i]:
            param.requires_grad = True

    # Step 4: Always unfreeze lm_head and decoder.layernorm_embedding
    for param in layer_groups["lm_head"]:
        param.requires_grad = True
    for param in layer_groups["decoder_layernorm"]:
        param.requires_grad = True

    timer_callback = TimerCallback()
    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)
    print(f"Average training time per epoch: {avg_epoch_time} s")

    return model, gpu_increase, avg_epoch_time

@torch.no_grad()
def translate_with_model(texts, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(texts, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    outputs = model.generate(**inputs, max_length=max_length)
    return tokenizer.batch_decode(outputs, skip_special_tokens=True), time.time()

def evaluate_model_by_category_from_testdata(model, tokenizer, test_data_with_category, batch_size=32, max_length=100):
    print("Evaluating model by category on provided test data...")
    chrf_metric = CHRF()
    category_scores = {}
    category_data = {}

    for hindi, english, category in test_data_with_category:
        category_data.setdefault(category, []).append((hindi, english))

    for category, data in category_data.items():
        print(f"\nProcessing category: {category} ({len(data)} examples)")
        all_meteor = []
        all_chrf = []

        for i in tqdm(range(0, len(data), batch_size), desc=f"Evaluating {category}"):
            batch = data[i:i + batch_size]
            hindi_batch = [x[0] for x in batch]
            ref_batch = [x[1] for x in batch]

            preds, _ = translate_with_model(hindi_batch, model, tokenizer, max_length=max_length)

            for ref, pred in zip(ref_batch, preds):
                ref_tokens = nltk.word_tokenize(ref.lower())
                pred_tokens = nltk.word_tokenize(pred.lower())

                meteor = meteor_score([ref_tokens], pred_tokens)
                chrf_score = chrf_metric.sentence_score(pred, [ref]).score / 100

                all_meteor.append(meteor)
                all_chrf.append(chrf_score)

        category_scores[category] = {
            'meteor': sum(all_meteor) / len(all_meteor) if all_meteor else 0.0,
            'chrf': sum(all_chrf) / len(all_chrf) if all_chrf else 0.0
        }

    return category_scores

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory = load_model()

    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
    full_data = load_full_dataset(base_path)

    if not full_data['train'] or not full_data['validation'] or not full_data['test']:
        print("Warning: Some splits have no data. Please check your dataset path and structure.")
        exit(1)

    train_dataset = prepare_dataset(full_data['train'], tokenizer)
    val_dataset = prepare_dataset(full_data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA on idiomatic and standard sentences.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model on the test set by category.")
    test_data = full_data['test']
    evaluation_results = evaluate_model_by_category_from_testdata(fine_tuned_model, tokenizer, test_data)

    results_df = pd.DataFrame.from_dict(evaluation_results, orient='index')
    results_df.index.name = "Category"
    results_df.columns = ['meteor_score', 'chrf_score']

    print("\nEvaluation Results by Category:")
    print(results_df.to_string())

    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv"
    results_df.to_csv(drive_csv_path)
    print(f"\nCategory-wise results saved to: {drive_csv_path}")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Original mBART model GPU memory usage: 2331.27 MB
Loading full dataset...
Processing train split - Standard Sentences...
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_present.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_past.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_future.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_perfect.csv
  Loaded 35 sentences from Standard Sentences/Exclamatory Sentences/simple_present.csv
  Load

Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...


Processing category: Idiomatic Sentences (469 examples)


Evaluating Idiomatic Sentences: 100%|██████████| 15/15 [00:36<00:00,  2.45s/it]



Processing category: Voice and Speech Constructions (540 examples)


Evaluating Voice and Speech Constructions: 100%|██████████| 17/17 [00:30<00:00,  1.79s/it]


Evaluation Results by Category:
                                meteor_score  chrf_score
Category                                                
Standard Sentences                  0.890692    0.844820
Idiomatic Sentences                 0.668149    0.571714
Voice and Speech Constructions      0.933209    0.901128

Category-wise results saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv


In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_full_dataset(base_path):
    """Load dataset and include category info for test set"""
    data = {'train': [], 'validation': [], 'test': []}

    set_mappings = {
        'train': 'train_set',
        'validation': 'validation_set',
        'test': 'test_set'
    }

    CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
    SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                      "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
    TENSES = [
        "simple_present.csv", "simple_past.csv", "simple_future.csv",
        "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
        "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
    ]

    print("Loading full dataset...")

    for split, folder_name in set_mappings.items():
        for category in CATEGORIES:
            split_path = os.path.join(base_path, folder_name, category)

            if not os.path.exists(split_path):
                print(f"Warning: Path {split_path} does not exist")
                continue

            print(f"Processing {split} split - {category}...")

            if category != "Voice and Speech Constructions":
                for sentence_type in SENTENCE_TYPES:
                    sentence_type_path = os.path.join(split_path, sentence_type)

                    if not os.path.exists(sentence_type_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(sentence_type_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{sentence_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")
            else:
                # Voice and Speech Constructions have different subtypes
                voice_types = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

                for voice_type in voice_types:
                    voice_path = os.path.join(split_path, voice_type)
                    if not os.path.exists(voice_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(voice_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{voice_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")


    print(f"Total loaded - Train: {len(data['train'])}, Validation: {len(data['validation'])}, Test: {len(data['test'])}")
    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    return model, tokenizer, gpu_increase

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def get_named_layer_groups(model):
    groups = {
        "embeddings": [],
        "encoder_layers": {},   # encoder_layers[layer_num]
        "decoder_layers": {},   # decoder_layers[layer_num]
        "lm_head": [],
        "decoder_layernorm": [],
        "other": []
    }

    for name, param in model.named_parameters():
        parts = name.split('.')

        if 'embed' in name:
            groups["embeddings"].append(param)

        elif 'encoder.layers' in name:
            # find index of 'layers' in parts
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["encoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                # fallback: put in 'other'
                groups["other"].append(param)

        elif 'decoder.layers' in name:
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["decoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                groups["other"].append(param)

        elif 'lm_head' in name:
            groups["lm_head"].append(param)

        elif 'decoder.layernorm_embedding' in name:
            groups["decoder_layernorm"].append(param)

        else:
            groups["other"].append(param)

    return groups

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)

    TOP_N = 2  # Unfreeze top N encoder & decoder layers

    # Get semantically grouped layers
    layer_groups = get_named_layer_groups(model)

    # # Step 1: Freeze everything
    # for param in model.parameters():
    #     param.requires_grad = False

    # Step 2: Unfreeze top N encoder layers
    encoder_layer_ids = sorted(layer_groups["encoder_layers"].keys())[-TOP_N:]
    for i in encoder_layer_ids:
        for param in layer_groups["encoder_layers"][i]:
            param.requires_grad = True

    # Step 3: Unfreeze top N decoder layers
    decoder_layer_ids = sorted(layer_groups["decoder_layers"].keys())[-TOP_N:]
    for i in decoder_layer_ids:
        for param in layer_groups["decoder_layers"][i]:
            param.requires_grad = True

    # Step 4: Always unfreeze lm_head and decoder.layernorm_embedding
    for param in layer_groups["lm_head"]:
        param.requires_grad = True
    for param in layer_groups["decoder_layernorm"]:
        param.requires_grad = True

    timer_callback = TimerCallback()
    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart2"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)
    print(f"Average training time per epoch: {avg_epoch_time} s")

    return model, gpu_increase, avg_epoch_time

@torch.no_grad()
def translate_with_model(texts, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(texts, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    outputs = model.generate(**inputs, max_length=max_length)
    return tokenizer.batch_decode(outputs, skip_special_tokens=True), time.time()

def evaluate_model_by_category_from_testdata(model, tokenizer, test_data_with_category, batch_size=32, max_length=100):
    print("Evaluating model by category on provided test data...")
    chrf_metric = CHRF()
    category_scores = {}
    category_data = {}

    for hindi, english, category in test_data_with_category:
        category_data.setdefault(category, []).append((hindi, english))

    for category, data in category_data.items():
        print(f"\nProcessing category: {category} ({len(data)} examples)")
        all_meteor = []
        all_chrf = []

        for i in tqdm(range(0, len(data), batch_size), desc=f"Evaluating {category}"):
            batch = data[i:i + batch_size]
            hindi_batch = [x[0] for x in batch]
            ref_batch = [x[1] for x in batch]

            preds, _ = translate_with_model(hindi_batch, model, tokenizer, max_length=max_length)

            for ref, pred in zip(ref_batch, preds):
                ref_tokens = nltk.word_tokenize(ref.lower())
                pred_tokens = nltk.word_tokenize(pred.lower())

                meteor = meteor_score([ref_tokens], pred_tokens)
                chrf_score = chrf_metric.sentence_score(pred, [ref]).score / 100

                all_meteor.append(meteor)
                all_chrf.append(chrf_score)

        category_scores[category] = {
            'meteor': sum(all_meteor) / len(all_meteor) if all_meteor else 0.0,
            'chrf': sum(all_chrf) / len(all_chrf) if all_chrf else 0.0
        }

    return category_scores

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory = load_model()

    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
    full_data = load_full_dataset(base_path)

    if not full_data['train'] or not full_data['validation'] or not full_data['test']:
        print("Warning: Some splits have no data. Please check your dataset path and structure.")
        exit(1)

    train_dataset = prepare_dataset(full_data['train'], tokenizer)
    val_dataset = prepare_dataset(full_data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA on idiomatic and standard sentences.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model on the test set by category.")
    test_data = full_data['test']
    evaluation_results = evaluate_model_by_category_from_testdata(fine_tuned_model, tokenizer, test_data)

    results_df = pd.DataFrame.from_dict(evaluation_results, orient='index')
    results_df.index.name = "Category"
    results_df.columns = ['meteor_score', 'chrf_score']

    print("\nEvaluation Results by Category:")
    print(results_df.to_string())

    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv"
    results_df.to_csv(drive_csv_path)
    print(f"\nCategory-wise results saved to: {drive_csv_path}")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Original mBART model GPU memory usage: 2331.27 MB
Loading full dataset...
Processing train split - Standard Sentences...
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_present.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_past.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_future.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_perfect.csv
  Loaded 35 sentences from Standard Sentences/Exclamatory Sentences/simple_present.csv
  Load

Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...


Processing category: Idiomatic Sentences (469 examples)


Evaluating Idiomatic Sentences: 100%|██████████| 15/15 [00:36<00:00,  2.46s/it]



Processing category: Voice and Speech Constructions (540 examples)


Evaluating Voice and Speech Constructions: 100%|██████████| 17/17 [00:30<00:00,  1.78s/it]


Evaluation Results by Category:
                                meteor_score  chrf_score
Category                                                
Standard Sentences                  0.897800    0.853821
Idiomatic Sentences                 0.678464    0.582546
Voice and Speech Constructions      0.937312    0.907319

Category-wise results saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv


In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_full_dataset(base_path):
    """Load dataset and include category info for test set"""
    data = {'train': [], 'validation': [], 'test': []}

    set_mappings = {
        'train': 'train_set',
        'validation': 'validation_set',
        'test': 'test_set'
    }

    CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
    SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                      "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
    TENSES = [
        "simple_present.csv", "simple_past.csv", "simple_future.csv",
        "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
        "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
    ]

    print("Loading full dataset...")

    for split, folder_name in set_mappings.items():
        for category in CATEGORIES:
            split_path = os.path.join(base_path, folder_name, category)

            if not os.path.exists(split_path):
                print(f"Warning: Path {split_path} does not exist")
                continue

            print(f"Processing {split} split - {category}...")

            if category != "Voice and Speech Constructions":
                for sentence_type in SENTENCE_TYPES:
                    sentence_type_path = os.path.join(split_path, sentence_type)

                    if not os.path.exists(sentence_type_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(sentence_type_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{sentence_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")
            else:
                # Voice and Speech Constructions have different subtypes
                voice_types = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

                for voice_type in voice_types:
                    voice_path = os.path.join(split_path, voice_type)
                    if not os.path.exists(voice_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(voice_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{voice_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")


    print(f"Total loaded - Train: {len(data['train'])}, Validation: {len(data['validation'])}, Test: {len(data['test'])}")
    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    return model, tokenizer, gpu_increase

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def get_named_layer_groups(model):
    groups = {
        "embeddings": [],
        "encoder_layers": {},   # encoder_layers[layer_num]
        "decoder_layers": {},   # decoder_layers[layer_num]
        "lm_head": [],
        "decoder_layernorm": [],
        "other": []
    }

    for name, param in model.named_parameters():
        parts = name.split('.')

        if 'embed' in name:
            groups["embeddings"].append(param)

        elif 'encoder.layers' in name:
            # find index of 'layers' in parts
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["encoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                # fallback: put in 'other'
                groups["other"].append(param)

        elif 'decoder.layers' in name:
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["decoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                groups["other"].append(param)

        elif 'lm_head' in name:
            groups["lm_head"].append(param)

        elif 'decoder.layernorm_embedding' in name:
            groups["decoder_layernorm"].append(param)

        else:
            groups["other"].append(param)

    return groups

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)

    TOP_N = 3  # Unfreeze top N encoder & decoder layers

    # Get semantically grouped layers
    layer_groups = get_named_layer_groups(model)

    # # Step 1: Freeze everything
    # for param in model.parameters():
    #     param.requires_grad = False

    # Step 2: Unfreeze top N encoder layers
    encoder_layer_ids = sorted(layer_groups["encoder_layers"].keys())[-TOP_N:]
    for i in encoder_layer_ids:
        for param in layer_groups["encoder_layers"][i]:
            param.requires_grad = True

    # Step 3: Unfreeze top N decoder layers
    decoder_layer_ids = sorted(layer_groups["decoder_layers"].keys())[-TOP_N:]
    for i in decoder_layer_ids:
        for param in layer_groups["decoder_layers"][i]:
            param.requires_grad = True

    # Step 4: Always unfreeze lm_head and decoder.layernorm_embedding
    for param in layer_groups["lm_head"]:
        param.requires_grad = True
    for param in layer_groups["decoder_layernorm"]:
        param.requires_grad = True

    timer_callback = TimerCallback()
    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart3"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)
    print(f"Average training time per epoch: {avg_epoch_time} s")

    return model, gpu_increase, avg_epoch_time

@torch.no_grad()
def translate_with_model(texts, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(texts, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    outputs = model.generate(**inputs, max_length=max_length)
    return tokenizer.batch_decode(outputs, skip_special_tokens=True), time.time()

def evaluate_model_by_category_from_testdata(model, tokenizer, test_data_with_category, batch_size=32, max_length=100):
    print("Evaluating model by category on provided test data...")
    chrf_metric = CHRF()
    category_scores = {}
    category_data = {}

    for hindi, english, category in test_data_with_category:
        category_data.setdefault(category, []).append((hindi, english))

    for category, data in category_data.items():
        print(f"\nProcessing category: {category} ({len(data)} examples)")
        all_meteor = []
        all_chrf = []

        for i in tqdm(range(0, len(data), batch_size), desc=f"Evaluating {category}"):
            batch = data[i:i + batch_size]
            hindi_batch = [x[0] for x in batch]
            ref_batch = [x[1] for x in batch]

            preds, _ = translate_with_model(hindi_batch, model, tokenizer, max_length=max_length)

            for ref, pred in zip(ref_batch, preds):
                ref_tokens = nltk.word_tokenize(ref.lower())
                pred_tokens = nltk.word_tokenize(pred.lower())

                meteor = meteor_score([ref_tokens], pred_tokens)
                chrf_score = chrf_metric.sentence_score(pred, [ref]).score / 100

                all_meteor.append(meteor)
                all_chrf.append(chrf_score)

        category_scores[category] = {
            'meteor': sum(all_meteor) / len(all_meteor) if all_meteor else 0.0,
            'chrf': sum(all_chrf) / len(all_chrf) if all_chrf else 0.0
        }

    return category_scores

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory = load_model()

    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
    full_data = load_full_dataset(base_path)

    if not full_data['train'] or not full_data['validation'] or not full_data['test']:
        print("Warning: Some splits have no data. Please check your dataset path and structure.")
        exit(1)

    train_dataset = prepare_dataset(full_data['train'], tokenizer)
    val_dataset = prepare_dataset(full_data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA on idiomatic and standard sentences.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model on the test set by category.")
    test_data = full_data['test']
    evaluation_results = evaluate_model_by_category_from_testdata(fine_tuned_model, tokenizer, test_data)

    results_df = pd.DataFrame.from_dict(evaluation_results, orient='index')
    results_df.index.name = "Category"
    results_df.columns = ['meteor_score', 'chrf_score']

    print("\nEvaluation Results by Category:")
    print(results_df.to_string())

    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv"
    results_df.to_csv(drive_csv_path)
    print(f"\nCategory-wise results saved to: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Original mBART model GPU memory usage: 2331.27 MB
Loading full dataset...
Processing train split - Standard Sentences...
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_present.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_past.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_future.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_perfect.csv
  Loaded 35 sentences from Standard Sentences/Exclamatory Sentences/simple_present.csv
  Load

Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...


Processing category: Idiomatic Sentences (469 examples)


Evaluating Idiomatic Sentences: 100%|██████████| 15/15 [00:37<00:00,  2.48s/it]



Processing category: Voice and Speech Constructions (540 examples)


Evaluating Voice and Speech Constructions: 100%|██████████| 17/17 [00:30<00:00,  1.78s/it]


Evaluation Results by Category:
                                meteor_score  chrf_score
Category                                                
Standard Sentences                  0.894812    0.856077
Idiomatic Sentences                 0.680712    0.581721
Voice and Speech Constructions      0.938145    0.907749

Category-wise results saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv


In [ ]:
import os
import pandas as pd
import torch
from torch.utils.data import DataLoader, Dataset
from transformers import MBartForConditionalGeneration, MBartTokenizer, Trainer, TrainingArguments, TrainerCallback
from datasets import Dataset
from peft import get_peft_model, LoraConfig, TaskType
import nltk
from nltk.translate.meteor_score import meteor_score
from sacrebleu.metrics import CHRF
from tqdm import tqdm
import time

# Download necessary NLTK data
nltk.download('punkt')
nltk.download('wordnet')

# Use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

def get_gpu_memory_usage():
    return torch.cuda.memory_allocated() / (1024 * 1024)  # in MB

def load_full_dataset(base_path):
    """Load dataset and include category info for test set"""
    data = {'train': [], 'validation': [], 'test': []}

    set_mappings = {
        'train': 'train_set',
        'validation': 'validation_set',
        'test': 'test_set'
    }

    CATEGORIES = ["Standard Sentences", "Idiomatic Sentences", "Voice and Speech Constructions"]
    SENTENCE_TYPES = ["Declarative Sentences", "Exclamatory Sentences", "Imperative Sentences",
                      "Interrogative Sentences", "Negation Sentences", "Complex Sentences", "Compound Sentences"]
    TENSES = [
        "simple_present.csv", "simple_past.csv", "simple_future.csv",
        "present_continuous.csv", "past_continuous.csv", "future_continuous.csv",
        "present_perfect.csv", "past_perfect.csv", "future_perfect.csv"
    ]

    print("Loading full dataset...")

    for split, folder_name in set_mappings.items():
        for category in CATEGORIES:
            split_path = os.path.join(base_path, folder_name, category)

            if not os.path.exists(split_path):
                print(f"Warning: Path {split_path} does not exist")
                continue

            print(f"Processing {split} split - {category}...")

            if category != "Voice and Speech Constructions":
                for sentence_type in SENTENCE_TYPES:
                    sentence_type_path = os.path.join(split_path, sentence_type)

                    if not os.path.exists(sentence_type_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(sentence_type_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{sentence_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")
            else:
                # Voice and Speech Constructions have different subtypes
                voice_types = ["Active Voice", "Passive Voice", "Direct Speech", "Indirect Speech"]

                for voice_type in voice_types:
                    voice_path = os.path.join(split_path, voice_type)
                    if not os.path.exists(voice_path):
                        continue

                    for tense_file in TENSES:
                        csv_path = os.path.join(voice_path, tense_file)

                        if not os.path.exists(csv_path):
                            continue

                        try:
                            df = pd.read_csv(csv_path)
                            hindi_sentences = df['Hindi_Text'].tolist()
                            english_sentences = df['English_Text'].tolist()

                            if split == 'test':
                                data[split].extend([(h, e, category) for h, e in zip(hindi_sentences, english_sentences)])
                            else:
                                data[split].extend(zip(hindi_sentences, english_sentences))

                            print(f"  Loaded {len(df)} sentences from {category}/{voice_type}/{tense_file}")
                        except Exception as e:
                            print(f"  Error loading {csv_path}: {e}")


    print(f"Total loaded - Train: {len(data['train'])}, Validation: {len(data['validation'])}, Test: {len(data['test'])}")
    return data

def load_model():
    print("Loading facebook/mbart-large-50-many-to-many-mmt model")
    model_checkpoint = "facebook/mbart-large-50-many-to-many-mmt"

    before_loading = get_gpu_memory_usage()

    tokenizer = MBartTokenizer.from_pretrained(model_checkpoint)
    model = MBartForConditionalGeneration.from_pretrained(model_checkpoint)
    model.to(device)

    after_loading = get_gpu_memory_usage()
    gpu_increase = after_loading - before_loading
    print(f"Original mBART model GPU memory usage: {gpu_increase:.2f} MB")

    return model, tokenizer, gpu_increase

def prepare_dataset(data, tokenizer):
    dataset = Dataset.from_dict({
        "hindi": [item[0] for item in data],
        "english": [item[1] for item in data]
    })

    def tokenize_function(examples):
        hindi_encodings = tokenizer(examples["hindi"], truncation=True, padding="max_length", max_length=128)
        english_encodings = tokenizer(examples["english"], truncation=True, padding="max_length", max_length=128)
        return {
            "input_ids": hindi_encodings["input_ids"],
            "attention_mask": hindi_encodings["attention_mask"],
            "labels": english_encodings["input_ids"],
        }

    tokenized_dataset = dataset.map(tokenize_function, batched=True, num_proc=os.cpu_count())
    return tokenized_dataset

class TimerCallback(TrainerCallback):
    def __init__(self):
        self.epoch_start_time = None
        self.epoch_times = []

    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()

    def on_epoch_end(self, args, state, control, **kwargs):
        epoch_time = time.time() - self.epoch_start_time
        self.epoch_times.append(epoch_time)
        print(f"Epoch {state.epoch} took {epoch_time:.2f} seconds")

def get_named_layer_groups(model):
    groups = {
        "embeddings": [],
        "encoder_layers": {},   # encoder_layers[layer_num]
        "decoder_layers": {},   # decoder_layers[layer_num]
        "lm_head": [],
        "decoder_layernorm": [],
        "other": []
    }

    for name, param in model.named_parameters():
        parts = name.split('.')

        if 'embed' in name:
            groups["embeddings"].append(param)

        elif 'encoder.layers' in name:
            # find index of 'layers' in parts
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["encoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                # fallback: put in 'other'
                groups["other"].append(param)

        elif 'decoder.layers' in name:
            try:
                idx = parts.index('layers')
                layer_num = int(parts[idx + 1])
                groups["decoder_layers"].setdefault(layer_num, []).append(param)
            except (ValueError, IndexError):
                groups["other"].append(param)

        elif 'lm_head' in name:
            groups["lm_head"].append(param)

        elif 'decoder.layernorm_embedding' in name:
            groups["decoder_layernorm"].append(param)

        else:
            groups["other"].append(param)

    return groups

def fine_tune_model(model, train_dataset, val_dataset):
    peft_config = LoraConfig(
        task_type=TaskType.SEQ_2_SEQ_LM,
        r=16,
        lora_alpha=512,
        lora_dropout=0.0,
        target_modules=["k_proj", "v_proj"]
    )

    before_lora = get_gpu_memory_usage()
    model = get_peft_model(model, peft_config)

    TOP_N = 4  # Unfreeze top N encoder & decoder layers

    # Get semantically grouped layers
    layer_groups = get_named_layer_groups(model)

    # # Step 1: Freeze everything
    # for param in model.parameters():
    #     param.requires_grad = False

    # Step 2: Unfreeze top N encoder layers
    encoder_layer_ids = sorted(layer_groups["encoder_layers"].keys())[-TOP_N:]
    for i in encoder_layer_ids:
        for param in layer_groups["encoder_layers"][i]:
            param.requires_grad = True

    # Step 3: Unfreeze top N decoder layers
    decoder_layer_ids = sorted(layer_groups["decoder_layers"].keys())[-TOP_N:]
    for i in decoder_layer_ids:
        for param in layer_groups["decoder_layers"][i]:
            param.requires_grad = True

    # Step 4: Always unfreeze lm_head and decoder.layernorm_embedding
    for param in layer_groups["lm_head"]:
        param.requires_grad = True
    for param in layer_groups["decoder_layernorm"]:
        param.requires_grad = True

    timer_callback = TimerCallback()
    training_args = TrainingArguments(
        output_dir="./results",
        num_train_epochs=5,
        per_device_train_batch_size=8,
        per_device_eval_batch_size=16,
        warmup_steps=500,
        weight_decay=0.01,
        logging_dir="./logs",
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="loss",
        greater_is_better=False,
        fp16=True,
        learning_rate=1e-4,
        report_to="none",
        save_safetensors=False
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        callbacks=[timer_callback],
    )

    trainer.train()

    after_training = get_gpu_memory_usage()
    gpu_increase = after_training - before_lora
    print(f"LoRA fine-tuned model additional GPU memory usage after training: {gpu_increase:.2f} MB")

    drive_save_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart4"
    model.save_pretrained(drive_save_path)
    print(f"Model saved to Google Drive: {drive_save_path}")

    avg_epoch_time = sum(timer_callback.epoch_times) / len(timer_callback.epoch_times)
    print(f"Average training time per epoch: {avg_epoch_time} s")

    return model, gpu_increase, avg_epoch_time

@torch.no_grad()
def translate_with_model(texts, model, tokenizer, max_length=100):
    model.eval()
    inputs = tokenizer(texts, return_tensors="pt", padding=True, truncation=True, max_length=max_length).to(device)
    outputs = model.generate(**inputs, max_length=max_length)
    return tokenizer.batch_decode(outputs, skip_special_tokens=True), time.time()

def evaluate_model_by_category_from_testdata(model, tokenizer, test_data_with_category, batch_size=32, max_length=100):
    print("Evaluating model by category on provided test data...")
    chrf_metric = CHRF()
    category_scores = {}
    category_data = {}

    for hindi, english, category in test_data_with_category:
        category_data.setdefault(category, []).append((hindi, english))

    for category, data in category_data.items():
        print(f"\nProcessing category: {category} ({len(data)} examples)")
        all_meteor = []
        all_chrf = []

        for i in tqdm(range(0, len(data), batch_size), desc=f"Evaluating {category}"):
            batch = data[i:i + batch_size]
            hindi_batch = [x[0] for x in batch]
            ref_batch = [x[1] for x in batch]

            preds, _ = translate_with_model(hindi_batch, model, tokenizer, max_length=max_length)

            for ref, pred in zip(ref_batch, preds):
                ref_tokens = nltk.word_tokenize(ref.lower())
                pred_tokens = nltk.word_tokenize(pred.lower())

                meteor = meteor_score([ref_tokens], pred_tokens)
                chrf_score = chrf_metric.sentence_score(pred, [ref]).score / 100

                all_meteor.append(meteor)
                all_chrf.append(chrf_score)

        category_scores[category] = {
            'meteor': sum(all_meteor) / len(all_meteor) if all_meteor else 0.0,
            'chrf': sum(all_chrf) / len(all_chrf) if all_chrf else 0.0
        }

    return category_scores

if __name__ == "__main__":
    print("Loading mBART model")
    model, tokenizer, original_model_memory = load_model()

    base_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/Translation Dataset Splitted (Old)"
    full_data = load_full_dataset(base_path)

    if not full_data['train'] or not full_data['validation'] or not full_data['test']:
        print("Warning: Some splits have no data. Please check your dataset path and structure.")
        exit(1)

    train_dataset = prepare_dataset(full_data['train'], tokenizer)
    val_dataset = prepare_dataset(full_data['validation'], tokenizer)

    print("Fine-tuning the model with LoRA on idiomatic and standard sentences.")
    fine_tuned_model, lora_memory_increase, avg_epoch_time = fine_tune_model(model, train_dataset, val_dataset)

    print("Evaluating the model on the test set by category.")
    test_data = full_data['test']
    evaluation_results = evaluate_model_by_category_from_testdata(fine_tuned_model, tokenizer, test_data)

    results_df = pd.DataFrame.from_dict(evaluation_results, orient='index')
    results_df.index.name = "Category"
    results_df.columns = ['meteor_score', 'chrf_score']

    print("\nEvaluation Results by Category:")
    print(results_df.to_string())

    drive_csv_path = "/content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv"
    results_df.to_csv(drive_csv_path)
    print(f"\nCategory-wise results saved to: {drive_csv_path}")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Using device: cuda
Loading mBART model
Loading facebook/mbart-large-50-many-to-many-mmt model


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'MBart50Tokenizer'. 
The class this function is called from is 'MBartTokenizer'.


Original mBART model GPU memory usage: 2331.27 MB
Loading full dataset...
Processing train split - Standard Sentences...
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_present.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_past.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/simple_future.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_continuous.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/present_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/past_perfect.csv
  Loaded 35 sentences from Standard Sentences/Declarative Sentences/future_perfect.csv
  Loaded 35 sentences from Standard Sentences/Exclamatory Sentences/simple_present.csv
  Load

Map (num_proc=2):   0%|          | 0/7105 [00:00<?, ? examples/s]

...


Processing category: Idiomatic Sentences (469 examples)


Evaluating Idiomatic Sentences: 100%|██████████| 15/15 [00:36<00:00,  2.42s/it]



Processing category: Voice and Speech Constructions (540 examples)


Evaluating Voice and Speech Constructions: 100%|██████████| 17/17 [00:30<00:00,  1.80s/it]


Evaluation Results by Category:
                                meteor_score  chrf_score
Category                                                
Standard Sentences                  0.891723    0.853794
Idiomatic Sentences                 0.679005    0.581258
Voice and Speech Constructions      0.937834    0.907008

Category-wise results saved to: /content/drive/MyDrive/Colab Notebooks/Translation Models/lora_partial_fine_tuned_mbart_category_scores.csv
